In [3]:
from flask import Flask
from flask_sqlalchemy import SQLAlchemy
from sqlalchemy import create_engine
import os
import pandas as pd

app = Flask(__name__)

engine = create_engine('sqlite:///recommender6.db', echo=False)

for f in os.listdir('data/movies/ml-latest-small'):
    if f[-4:] == '.csv':
        data = pd.read_csv(f'data/movies/ml-latest-small/{f}')
        data.to_sql(f[:-4], engine)
        print(f[0:-4])

links
ratings
movies
tags


In [4]:
watched_movie_id_list = ['70286', '109487', '589']

In [5]:
import numpy as np

movie_id_unique = 'SELECT * FROM movies'
all_movies = pd.read_sql(movie_id_unique, engine)

#remove the input movies from all_movies
movies_not_watched = all_movies[~all_movies['movieId'].isin(watched_movie_id_list)]
movies_not_watched.loc[:,'fake_id'] = np.ones(len(movies_not_watched), dtype =int)

#get all_ratings from sqlite
query = 'SELECT "userId", ratings."movieId", movies.title, rating FROM ratings JOIN movies ON ratings."movieId" = movies."movieId";'
all_ratings = pd.read_sql(query, engine)

#remove the watched movies from all_ratings
not_all_ratings = all_ratings[~all_ratings['movieId'].isin(watched_movie_id_list)]

#remove movieId and ratings of the watched movies???
movieindex = not_all_ratings['movieId'].unique().tolist()
dl_movie2movie_encoded = {x: i for i, x in enumerate(movieindex)}
dl_movie_encoded2movie = {i: x for i, x in enumerate(movieindex)}

not_all_ratings.loc[:,"movie"] = not_all_ratings["movieId"].map(dl_movie2movie_encoded)
not_all_ratings.loc[:,"rating"] = not_all_ratings["rating"].values.astype(np.float32)

#map userId from ?? to not_all_ratings ?? what do i do with the users??

not_all_user_ids = not_all_ratings["userId"].unique().tolist()
dl_user2user_encoded = {x: i for i, x in enumerate(not_all_user_ids)}
dl_userencoded2user = {i: x for i, x in enumerate(not_all_user_ids)}

not_all_ratings.loc[:,"user"] = not_all_ratings["userId"].map(dl_user2user_encoded)

min_rating = min(not_all_ratings["rating"])
max_rating = max(not_all_ratings["rating"])
num_users = len(dl_user2user_encoded)
num_movies = len(dl_movie_encoded2movie)
print(
        "Number of users: {}, Number of Movies: {}, Min rating: {}, Max rating: {}".format(
            num_users, num_movies, min_rating, max_rating
        )
    )

#define training data
df = not_all_ratings.sample(frac=1, random_state=42)
x = not_all_ratings[["user", "movie"]].values

    # Normalize the targets between 0 and 1. Makes it easy to train.
y = not_all_ratings["rating"].apply(lambda x: (x - min_rating) / (max_rating - min_rating)).values
    # Assuming training on 90% of the data and validating on 10%.
train_indices = int(0.9 * df.shape[0])
x_train, x_val, y_train, y_val = (
        x[:train_indices],
        x[train_indices:],
        y[:train_indices],
        y[train_indices:],
    )

#inference
user_movie_array = movies_not_watched[['fake_id','index']]
max_movie_index = user_movie_array['index'].max()
that = user_movie_array.to_numpy()

EMBEDDING_SIZE = 50

import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers

class RecommenderNet(keras.Model):
        def __init__(self, num_users, num_movies, embedding_size, **kwargs):
            super(RecommenderNet, self).__init__(**kwargs)
            self.num_users = num_users
            self.num_movies = num_movies
            self.embedding_size = embedding_size
            self.user_embedding = layers.Embedding(
                num_users,
                embedding_size,
                embeddings_initializer="he_normal",
                embeddings_regularizer=keras.regularizers.l2(1e-6),
            )
            self.user_bias = layers.Embedding(num_users, 1)
            self.movie_embedding = layers.Embedding(
            #change this line from num_movies to max_movie_index+1
                max_movie_index+1,
                embedding_size,
                embeddings_initializer="he_normal",
                embeddings_regularizer=keras.regularizers.l2(1e-6),
            )
            #and this line (input_dim)
            self.movie_bias = layers.Embedding(max_movie_index+1, 1)

        def call(self, inputs):
            user_vector = self.user_embedding(inputs[:, 0])
            user_bias = self.user_bias(inputs[:, 0])
            movie_vector = self.movie_embedding(inputs[:, 1])
            movie_bias = self.movie_bias(inputs[:, 1])
            dot_user_movie = tf.tensordot(user_vector, movie_vector, 2)
            # Add all the components (including bias)
            x = dot_user_movie + user_bias + movie_bias
            # The sigmoid activation forces the rating to between 0 and 1
            return tf.nn.sigmoid(x)
            #return movie_bias

model = RecommenderNet(num_users, num_movies, EMBEDDING_SIZE)
model.compile(
        loss=tf.keras.losses.BinaryCrossentropy(), optimizer=keras.optimizers.Adam(lr=0.001)
    )
ratings = model.predict(that).flatten()

movies_not_watched.loc[:,'prediction'] = ratings
highest_score = ratings[ratings.argsort()[-10:]][::-1]

recom_movie_titles = movies_not_watched.loc[movies_not_watched.loc[:,'prediction'].isin(highest_score)]
#movies_not_watched.loc[movies_not_watched['index'].isin(top_ratings_indices)]
recom_movie_titles


/opt/conda/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = _infer_fill_value(value)
/opt/conda/lib/python3.8/site-packages/pandas/core/indexing.py:1743: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(ilocs[0], value)


Number of users: 610, Number of Movies: 9721, Min rating: 0.5, Max rating: 5.0


/opt/conda/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = _infer_fill_value(value)
/opt/conda/lib/python3.8/site-packages/pandas/core/indexing.py:1743: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(ilocs[0], value)


index  movieId                                              title  \
3715   3715     5131             How to Kill Your Neighbor's Dog (2000)   
3717   3717     5135                             Monsoon Wedding (2001)   
3720   3720     5139                         Bad News Bears, The (1976)   
3721   3721     5146  Vampire Hunter D: Bloodlust (Banpaia hantâ D) ...   
3723   3723     5151                       40 Days and 40 Nights (2002)   
3727   3727     5159              Ferngully: The Last Rainforest (1992)   
3732   3732     5177                  Magnificent Ambersons, The (1942)   
3737   3737     5197                             Little Darlings (1980)   
3740   3740     5205                                  Motel Hell (1980)   
3742   3742     5212                                Octagon, The (1980)   

                                 genres  fake_id  prediction  
3715                       Comedy|Drama        1    0.533238  
3717                     Comedy|Romance        1    0.531017  
3720                             Comedy        1    0.533113  
3721    Animation|Fantasy|Horror|Sci-Fi        1    0.527727  
3723                     Comedy|Romance        1    0.532211  
3727  Animation|Children|Comedy|Musical        1    0.530114  
3732                      Drama|Romance        1    0.527418  
3737                              Drama        1    0.530616  
3740                      Comedy|Horror        1    0.529562  
3742                             Action        1    0.532292

In [ ]:
first have to replace Sci-Fi with SciFi and Film-Noir with FilmNoir otherwise the len(np.unique(genres)) is wrong

In [6]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

all_movies['genres'].replace('Sci-Fi', 'SciFi', inplace=True, regex=True)
all_movies['genres'].replace('Film-Noir', 'FilmNoir', inplace=True, regex=True)
all_movies['genres'].replace('(no genres listed)', 'N/A', inplace=True, regex=True)
all_movies['genres'][300:350]
allgenres = all_movies['genres']
tfidf_vectorizer=TfidfVectorizer()
tfidf_matrix=tfidf_vectorizer.fit_transform(allgenres)

print(tfidf_vectorizer.get_feature_names())

#ไม่ได้ใช้ แค่ปริ๊นมาดูเล่นเพื่อเช็คตัวเล็กตัวใหญ่

['action', 'adventure', 'animation', 'children', 'comedy', 'crime', 'documentary', 'drama', 'fantasy', 'filmnoir', 'horror', 'imax', 'musical', 'mystery', 'romance', 'scifi', 'thriller', 'war', 'western']


In [7]:
tfidf_matrix

<9742x19 sparse matrix of type '<class 'numpy.float64'>'
	with 22050 stored elements in Compressed Sparse Row format>

In [8]:
liked_genres = all_movies.loc[all_movies['movieId'].isin(watched_movie_id_list), 'genres'].to_list()
liked_genres

['Action|SciFi', 'Mystery|SciFi|Thriller', 'SciFi|IMAX']

In [9]:
splitted = [sub.split("|") for sub in liked_genres]
flat_list = []
for sublist in splitted:
    for item in sublist:
        flat_list.append(item)
flat_list

['Action', 'SciFi', 'Mystery', 'SciFi', 'Thriller', 'SciFi', 'IMAX']

In [10]:
vocab = []
for item in flat_list:
    perrow = item.lower()
    vocab.append(perrow)
vocab

['action', 'scifi', 'mystery', 'scifi', 'thriller', 'scifi', 'imax']

In [11]:
#why i didn't use tfidf

vectoriser2 = tfidf_vectorizer.fit_transform(vocab)
vectoriser2

<7x5 sparse matrix of type '<class 'numpy.float64'>'
	with 7 stored elements in Compressed Sparse Row format>

In [ ]:
if fit_transform doesn't have vocabulary_

In [12]:
vectoriser2 = tfidf_vectorizer.fit(vocab)
vectoriser2

TfidfVectorizer()

In [13]:
vectoriser2.vocabulary_

{'action': 0, 'scifi': 3, 'mystery': 2, 'thriller': 4, 'imax': 1}

In [17]:
vectoriser3 = CountVectorizer().fit(vocab)
vectoriser3.vocabulary_ # show the word-matrix position pairs

{'action': 0, 'scifi': 3, 'mystery': 2, 'thriller': 4, 'imax': 1}

In [18]:
vectoriser3

CountVectorizer()

In [19]:
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

def vect_cos(vect, test_list):

    """ Vectorise text and compute the cosine similarity """
    query_0 = vect.transform([' '.join(vect.get_feature_names())])
    query_1 = vect.transform(test_list)
    cos_sim = cosine_similarity(query_0.A, query_1.A)  # displays the resulting matrix
    return query_1, np.round(cos_sim.squeeze(), 3)


In [24]:
#cosine_similarity comes out too but it doesn't give higher score to scifi in particular

#have to fix this use iterrow or something, not forloop in a dataframe
bag = []
for i in all_movies.genres:
    i_splitted = i.split("|")
    genre = [genre.lower() for genre in i_splitted]
    tfidf_vect, tfidf_cos = vect_cos(vectoriser2, [' '.join(genre)])
    bag.append(tfidf_cos)
    print(tfidf_cos)

pd.DataFrame(bag)

0.0
0.0
0.0
0.0
0.0
0.666
0.0
0.0
0.471
0.666
0.0
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.666
0.471
0.666
0.666
0.334
0.0
0.0
0.0
0.0
0.578
0.0
0.0
0.746
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.471
0.471
0.0
0.666
0.0
0.0
0.666
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.746
0.0
0.0
0.666
0.471
0.0
0.0
0.0
0.0
0.746
0.0
0.666
0.471
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.0
0.666
0.471
0.0
0.0
0.666
0.0
0.0
0.0
0.471
0.0
0.0
0.746
0.0
0.0
0.0
0.0
0.0
0.471
0.471
0.471
0.471
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.0
0.666
0.0
0.0
0.0
0.471
0.471
0.471
0.0
0.471
0.0
0.0
0.0
0.0
0.0
0.471
0.746
0.471
0.0
0.471
0.666
0.666
0.0
0.471
0.0
0.666
0.0
0.746
0.578
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.471
0.0
0.666
0.0
0.0
0.471
0.0
0.471
0.0
0.0
0.0
0.0
0.334
0.882
0.0
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.578
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.666
0.0
0.471
0.471
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.471


0.471
0.0
0.471
0.0
0.578
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.666
0.666
0.666
0.471
0.471
0.334
0.334
0.471
0.471
0.471
0.471
0.666
0.816
0.0
0.0
0.0
0.0
0.471
0.0
0.471
0.471
0.0
0.0
0.0
0.471
0.334
0.666
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.334
0.334
0.0
0.0
0.578
0.578
0.334
0.471
0.0
0.0
0.0
0.0
0.0
0.0
0.666
0.666
0.0
0.0
0.471
0.0
0.0
0.0
0.816
0.471
0.0
0.0
0.0
0.0
0.471
0.0
0.471
0.666
0.0
0.0
0.0
0.0
0.334
0.0
0.0
0.334
0.0
0.0
0.0
0.0
0.0
0.666
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.666
0.0
0.471
0.666
0.578
0.334
0.746
0.578
0.578
0.578
0.578
0.578
0.578
0.471
0.666
0.0
0.0
0.0
0.666
0.0
0.471
0.0
0.0
0.0
0.578
0.471
0.471
0.0
0.578
0.578
0.0
0.471
0.0
0.0
0.471
0.471
0.0
0.0
0.0
0.0
0.471
0.0
0.746
0.0
0.0
0.0
0.0
0.0
0.666
0.0
0.0
0.471
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.578
0.0
0.0
0.0
0.0
0.746
0.471
0.0
0.0
0.0
0.0
0.0
0.334
0.578
0.334
0.471
0.666
0.0
0.0
0.0
0.0
0.0
0.746
0.578
0.0
0.0
0.471
0.0
0.0
0.0
0.578
0.578
0.578
0.578
0.0
0.334
0.0
0.0
0.0
0.0
0.334


0.0
0.471
0.666
0.471
0.0
0.0
0.0
0.578
0.471
0.0
0.746
0.471
0.0
0.0
0.0
0.471
0.0
0.746
0.0
0.0
0.0
0.471
0.0
0.666
0.0
0.0
0.666
0.471
0.0
0.334
0.0
0.0
0.0
0.471
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.666
0.0
0.0
0.666
0.0
0.578
0.578
0.334
0.0
0.666
0.471
0.471
0.334
0.334
0.0
0.666
0.471
0.471
0.0
0.0
0.0
0.471
0.0
0.666
0.578
0.0
0.471
0.0
0.0
0.0
0.0
0.746
0.0
0.0
0.666
0.0
0.334
0.0
0.471
0.578
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.471
0.666
0.0
0.471
0.0
0.0
0.471
0.0
0.0
0.0
0.666
0.0
0.0
0.816
0.666
0.0
0.471
0.0
0.471
0.471
0.0
0.746
0.471
0.0
0.471
0.0
0.0
0.578
0.471
0.0
0.0
0.746
0.0
0.666
0.666
0.0
0.0
0.471
0.0
0.334
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.666
0.578
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.0
0.471
0.0
0.471
0.471
0.0
0.0
0.0
0.0
0.666
0.0
0.666
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.334
0.0
0.0
0.471
0.471
0.471
0.0
0.0
0.0
0.471
0.578
0.0
0.0
0.746
0.0
0.334
0.0
0.471
0.0
0.0
0.666
0.471
0.0
0.0
0.0
0.746
0.471
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.471
0.47

0.666
0.0
0.334
0.0
0.0
0.0
0.0
0.746
0.0
0.0
0.471
0.0
0.578
0.471
0.471
0.0
0.471
0.471
0.0
0.0
0.0
0.0
0.816
0.746
0.0
0.578
0.0
0.0
0.746
0.0
0.0
0.0
0.666
0.0
0.666
0.0
0.0
0.0
0.666
0.0
0.0
0.471
0.334
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.578
0.0
0.0
0.666
0.0
0.0
0.666
0.0
0.0
0.0
0.471
0.666
0.0
0.471
0.471
0.0
0.471
0.0
0.0
0.666
0.0
0.0
0.816
0.471
0.0
0.471
0.0
0.0
0.0
0.0
0.471
0.666
0.666
0.0
0.0
0.0
0.334
0.578
0.334
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.471
0.471
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.666
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.334
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.471
0.471
0.0
0.666
0.0
0.471
0.666
0.0
0.0
0.0
0.471
0.471
0.0
0.816
0.0
0.0
0.0
0.471
0.578
0.471
0.0
0.0
0.0
0.471
0.0
0.471
0.666
0.0
0.0
0.471
0.0
0.578
0.0
0.471
0.471
0.0
0.0
0.471
0.471
0.334
0.471
0.0
0.0
0.334
0.471
0.471
0.334
0.0
0.0
0.578
0.0
0.816
0.

0.471
0.0
0.471
0.0
0.666
0.0
0.471
0.0
0.0
0.0
0.0
0.471
0.578
0.0
0.471
0.0
0.0
0.0
0.334
0.0
0.666
0.0
0.0
0.666
0.746
0.0
0.0
0.0
0.471
0.471
0.666
0.0
0.0
0.0
0.471
0.0
0.0
0.471
0.666
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.666
0.0
0.471
0.471
0.746
0.0
0.471
0.578
0.0
0.746
0.666
0.471
0.0
0.334
0.578
0.0
0.0
0.334
0.0
0.0
0.0
0.0
0.471
0.0
0.471
0.666
0.0
0.0
0.0
0.0
0.0
0.471
0.666
0.334
0.334
0.471
0.578
0.0
0.578
0.0
0.471
0.471
0.578
0.471
0.0
0.471
0.746
0.471
0.0
0.0
0.334
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.0
0.0
0.578
0.334
0.666
0.471
0.0
0.0
0.746
0.471
0.471
0.0
0.0
0.0
0.0
0.0
0.471
0.471
0.0
0.471
0.0
0.0
0.0
0.471
0.0
0.746
0.0
0.746
0.666
0.471
0.666
0.666
0.471
0.0
0.0
0.0
0.471
0.578
0.0
0.0
0.746
0.0
0.0
0.471
0.666
0.0
0.666
0.471
0.666
0.666
0.0
0.471
0.0
0.0
0.0
0.0
0.0
0.334
0.0
0.0
0.471
0.0
0.0
0.471
0.0
0.0
0.471
0.746
0.0
0.816
0.0
0.0
0.0
0.0
0.471
0.0
0.666
0.0
0.0
0.471
0.666
0.0
0.0
0.0
0.666
0.471
0.0
0.0
0.471
0.471
0.0
0.666
0.0
0.471
0.0
0.0
0.0
0.471


0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.471
0.746
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.666
0.471
0.0
0.578
0.666
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.0
0.578
0.0
0.334
0.334
0.0
0.471
0.0
0.0
0.471
0.0
0.578
0.0
0.0
0.471
0.0
0.0
0.578
0.666
0.666
0.0
0.0
0.666
0.0
0.334
0.0
0.0
0.666
0.746
0.0
0.578
0.334
0.334
0.666
0.666
0.0
0.334
0.578
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.471
0.666
0.0
0.0
0.0
0.471
0.0
0.471
0.0
0.0
0.0
0.0
0.0
0.746
0.0
0.0
0.471
0.0
0.0
0.578
0.471
0.0
0.0
0.471
0.0
0.0
0.0
0.816
0.0
0.666
0.0
0.0
0.0
0.666
0.334
0.0
0.471
0.578
0.0
0.0
0.0
0.0
0.0
0.334
0.0
0.471
0.471
0.666
0.471
0.471
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.334
0.471
0.578
0.0
0.0
0.666
0.0
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.471
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.334
0.578
0.0
0.0
0.334
0.471
0.0
0.578
0.882
0.471
0.0
0.578
0.578
0.578
0.0
0.0
0.471
0.471
0.0
0.334
0.0
0.471
0.666
0.0
0.0
0.471
0.471
0.471
0.334
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.578
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.47

0
0     0.000
1     0.000
2     0.000
3     0.000
4     0.000
...     ...
9737  0.471
9738  0.000
9739  0.000
9740  0.471
9741  0.000

[9742 rows x 1 columns]

In [ ]:
vectoriser3 = CountVectorizer().fit(vocab)
vectoriser3.vocabulary_ # show the word-matrix position pairs

In [22]:
tfidf_cos

0.0

In [26]:
tfidf_vect, tfidf_cos = vect_cos(vectoriser2, [' '.join(genre)])
genre_bias = pd.DataFrame(bag)
genre_bias
#ถุงใส่ค่า cosine_similarity ระหว่างไม้บรรทัดกับแต่ละบรรทัด วัดมาแล้วใส่ถุงมาส่ง
# เออ ส่งนี้ไปเลย ให้กลับไปไฟล์หลัก

0
0     0.000
1     0.000
2     0.000
3     0.000
4     0.000
...     ...
9737  0.471
9738  0.000
9739  0.000
9740  0.471
9741  0.000

[9742 rows x 1 columns]

In [27]:
movies_not_watched = all_movies[~all_movies['movieId'].isin(watched_movie_id_list)]
movies_not_watched

index  movieId                                      title  \
0         0        1                           Toy Story (1995)   
1         1        2                             Jumanji (1995)   
2         2        3                    Grumpier Old Men (1995)   
3         3        4                   Waiting to Exhale (1995)   
4         4        5         Father of the Bride Part II (1995)   
...     ...      ...                                        ...   
9737   9737   193581  Black Butler: Book of the Atlantic (2017)   
9738   9738   193583               No Game No Life: Zero (2017)   
9739   9739   193585                               Flint (2017)   
9740   9740   193587        Bungo Stray Dogs: Dead Apple (2018)   
9741   9741   193609        Andrew Dice Clay: Dice Rules (1991)   

                                           genres  
0     Adventure|Animation|Children|Comedy|Fantasy  
1                      Adventure|Children|Fantasy  
2                                  Comedy|Romance  
3                            Comedy|Drama|Romance  
4                                          Comedy  
...                                           ...  
9737              Action|Animation|Comedy|Fantasy  
9738                     Animation|Comedy|Fantasy  
9739                                        Drama  
9740                             Action|Animation  
9741                                       Comedy  

[9739 rows x 4 columns]

In [28]:

movies_not_watched = pd.concat([movies_not_watched, genre_bias], axis=1)
movies_not_watched.columns = ['index', 'movieId', 'title', 'genres', 'genre_bias']

In [29]:
movies_not_watched #พร้อมจะเอาไปคูณกับ prediction แล้วจ้า 
#เอา genre_bias ส่งคืนให้ไฟล์โมเดล ในรูป movies_not_watched['genre_bias']

index   movieId                                      title  \
0        0.0       1.0                           Toy Story (1995)   
1        1.0       2.0                             Jumanji (1995)   
2        2.0       3.0                    Grumpier Old Men (1995)   
3        3.0       4.0                   Waiting to Exhale (1995)   
4        4.0       5.0         Father of the Bride Part II (1995)   
...      ...       ...                                        ...   
9737  9737.0  193581.0  Black Butler: Book of the Atlantic (2017)   
9738  9738.0  193583.0               No Game No Life: Zero (2017)   
9739  9739.0  193585.0                               Flint (2017)   
9740  9740.0  193587.0        Bungo Stray Dogs: Dead Apple (2018)   
9741  9741.0  193609.0        Andrew Dice Clay: Dice Rules (1991)   

                                           genres  genre_bias  
0     Adventure|Animation|Children|Comedy|Fantasy       0.000  
1                      Adventure|Children|Fantasy       0.000  
2                                  Comedy|Romance       0.000  
3                            Comedy|Drama|Romance       0.000  
4                                          Comedy       0.000  
...                                           ...         ...  
9737              Action|Animation|Comedy|Fantasy       0.471  
9738                     Animation|Comedy|Fantasy       0.000  
9739                                        Drama       0.000  
9740                             Action|Animation       0.471  
9741                                       Comedy       0.000  

[9742 rows x 5 columns]

In [96]:
import numpy as np

movie_id_unique = 'SELECT * FROM movies'
all_movies = pd.read_sql(movie_id_unique, engine)

#remove the input movies from all_movies
movies_not_watched = all_movies[~all_movies['movieId'].isin(watched_movie_id_list)]
movies_not_watched.loc[:,'fake_id'] = np.ones(len(movies_not_watched), dtype =int)

#get all_ratings from sqlite
query = 'SELECT "userId", ratings."movieId", movies.title, rating FROM ratings JOIN movies ON ratings."movieId" = movies."movieId";'
all_ratings = pd.read_sql(query, engine)

#remove the watched movies from all_ratings
not_all_ratings = all_ratings[~all_ratings['movieId'].isin(watched_movie_id_list)]

#remove movieId and ratings of the watched movies???
movieindex = not_all_ratings['movieId'].unique().tolist()
dl_movie2movie_encoded = {x: i for i, x in enumerate(movieindex)}
dl_movie_encoded2movie = {i: x for i, x in enumerate(movieindex)}

not_all_ratings.loc[:,"movie"] = not_all_ratings["movieId"].map(dl_movie2movie_encoded)
not_all_ratings.loc[:,"rating"] = not_all_ratings["rating"].values.astype(np.float32)

#map userId from ?? to not_all_ratings ?? what do i do with the users??

not_all_user_ids = not_all_ratings["userId"].unique().tolist()
dl_user2user_encoded = {x: i for i, x in enumerate(not_all_user_ids)}
dl_userencoded2user = {i: x for i, x in enumerate(not_all_user_ids)}

not_all_ratings.loc[:,"user"] = not_all_ratings["userId"].map(dl_user2user_encoded)

min_rating = min(not_all_ratings["rating"])
max_rating = max(not_all_ratings["rating"])
num_users = len(dl_user2user_encoded)
num_movies = len(dl_movie_encoded2movie)
print(
        "Number of users: {}, Number of Movies: {}, Min rating: {}, Max rating: {}".format(
            num_users, num_movies, min_rating, max_rating
        )
    )

#define training data
df = not_all_ratings.sample(frac=1, random_state=42)
x = not_all_ratings[["user", "movie"]].values

    # Normalize the targets between 0 and 1. Makes it easy to train.
y = not_all_ratings["rating"].apply(lambda x: (x - min_rating) / (max_rating - min_rating)).values
    # Assuming training on 90% of the data and validating on 10%.
train_indices = int(0.9 * df.shape[0])
x_train, x_val, y_train, y_val = (
        x[:train_indices],
        x[train_indices:],
        y[:train_indices],
        y[train_indices:],
    )

#inference
user_movie_array = movies_not_watched[['fake_id','index']]
max_movie_index = user_movie_array['index'].max()
that = user_movie_array.to_numpy()

EMBEDDING_SIZE = 50

import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers

class RecommenderNet(keras.Model):
        def __init__(self, num_users, num_movies, embedding_size, **kwargs):
            super(RecommenderNet, self).__init__(**kwargs)
            self.num_users = num_users
            self.num_movies = num_movies
            self.embedding_size = embedding_size
            self.user_embedding = layers.Embedding(
                num_users,
                embedding_size,
                embeddings_initializer="he_normal",
                embeddings_regularizer=keras.regularizers.l2(1e-6),
            )
            self.user_bias = layers.Embedding(num_users, 1)
            self.movie_embedding = layers.Embedding(
            #change this line from num_movies to max_movie_index+1
                max_movie_index+1,
                embedding_size,
                embeddings_initializer="he_normal",
                embeddings_regularizer=keras.regularizers.l2(1e-6),
            )
            #and this line (input_dim)
            self.movie_bias = layers.Embedding(max_movie_index+1, 1)

        def call(self, inputs):
            user_vector = self.user_embedding(inputs[:, 0])
            user_bias = self.user_bias(inputs[:, 0])
            movie_vector = self.movie_embedding(inputs[:, 1])
            movie_bias = self.movie_bias(inputs[:, 1])
            dot_user_movie = tf.tensordot(user_vector, movie_vector, 2)
            # Add all the components (including bias)
            x = dot_user_movie + user_bias + movie_bias
            # The sigmoid activation forces the rating to between 0 and 1
            return tf.nn.sigmoid(x)
            #return movie_bias

model = RecommenderNet(num_users, num_movies, EMBEDDING_SIZE)
model.compile(
        loss=tf.keras.losses.BinaryCrossentropy(), optimizer=keras.optimizers.Adam(lr=0.001)
    )
ratings = model.predict(that).flatten()

movies_not_watched.loc[:,'prediction'] = ratings
#highest_score = ratings[ratings.argsort()[-10:]][::-1]

#recom_movie_titles = movies_not_watched.loc[movies_not_watched.loc[:,'prediction'].isin(highest_score)]
#movies_not_watched.loc[movies_not_watched['index'].isin(top_ratings_indices)]
#recom_movie_titles

#add genre_bias back here this line
movies_not_watched = pd.concat([movies_not_watched, genre_bias], axis=1) #genre_bias คือสิ่งที่เราคำนวณมาแทบตาย
movies_not_watched.columns = ['index', 'movieId', 'title', 'genres','fake_id', 'prediction', 'genre_bias']


movies_not_watched.loc[:,'prediction with genres bias'] = movies_not_watched['prediction']* movies_not_watched['genre_bias']

#movies_not_watched['prediction with genres bias'] = ratings_with_genre_bias
#ratings_with_genre_bias
#newhighscore = ratings_with_genre_bias[ratings_with_genre_bias.argsort()[-10:]][::-1]
#newhighscore #ทำไมถึงผิดล่ะ ทำไม argsort ไม่ได้เหมือนก่อน
#recom_movie_titles = movies_not_watched.loc[movies_not_watched.loc[:,'prediction'].isin(newhighscore)]
#recom_movie_titles = movies_not_watched.loc[movies_not_watched.loc[:,'prediction with genre bias'].isin(newhighscore)]
#recom_movie_titles

ratings = movies_not_watched.loc[:,'prediction']
highest_score = ratings[ratings.argsort()[-10:]][::-1]

recom_movie_titles = movies_not_watched.loc[movies_not_watched.loc[:,'prediction'].isin(highest_score)]
#movies_not_watched.loc[movies_not_watched['index'].isin(top_ratings_indices)]
print(recom_movie_titles)



movies_not_watched_with_bias = movies_not_watched.sort_values(by=['prediction with genres bias'], ascending=False)
movies_not_watched_with_bias[0:10]
#เอาแบบนี้เลยละกัน ไม่ได้สิ มันจะเอา recom_movie_titles

#ทำไมปริ๊นดาต้าเฟรมไม่ได้วะ แต่วันนี้ไม่มีอารมณ์แก้แล้ว อยากเห็นแต่ผลลัพธ์ของ recommender with genre bias :D

/opt/conda/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = _infer_fill_value(value)
/opt/conda/lib/python3.8/site-packages/pandas/core/indexing.py:1743: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(ilocs[0], value)


Number of users: 610, Number of Movies: 9721, Min rating: 0.5, Max rating: 5.0
       index  movieId                                        title  \
3103  3103.0   4166.0              Series 7: The Contenders (2001)   
3105  3105.0   4168.0                           Get Over It (2001)   
3108  3108.0   4175.0                        Gray's Anatomy (1996)   
3112  3112.0   4184.0                    Bishop's Wife, The (1947)   
3121  3121.0   4198.0               Battle Beyond the Stars (1980)   
3124  3124.0   4203.0  Harley Davidson and the Marlboro Man (1991)   
3134  3134.0   4218.0                          River's Edge (1986)   
3140  3140.0   4225.0                             Dish, The (2001)   
4884  4884.0   7317.0                              EuroTrip (2004)   
4894  4894.0   7328.0    Passion of Anna, The (Passion, En) (1969)   

                    genres  fake_id  prediction  genre_bias  \
3103          Action|Drama      1.0    0.528929       0.471   
3105        Comedy|Roman

index   movieId                           title  \
7372  7372.0   79132.0                Inception (2010)   
6797  6797.0   60684.0                 Watchmen (2009)   
3873  3873.0    5445.0          Minority Report (2002)   
8238  8238.0  104243.0                  Riddick (2013)   
6521  6521.0   53996.0             Transformers (2007)   
7866  7866.0   94018.0               Battleship (2012)   
4639  4639.0    6934.0  Matrix Revolutions, The (2003)   
7562  7562.0   85414.0              Source Code (2011)   
4351  4351.0    6365.0     Matrix Reloaded, The (2003)   
8151  8151.0  102125.0               Iron Man 3 (2013)   

                                               genres  fake_id  prediction  \
7372  Action|Crime|Drama|Mystery|Sci-Fi|Thriller|IMAX      1.0    0.517460   
6797        Action|Drama|Mystery|Sci-Fi|Thriller|IMAX      1.0    0.513101   
3873             Action|Crime|Mystery|Sci-Fi|Thriller      1.0    0.525466   
8238                      Action|Sci-Fi|Thriller|IMAX      1.0    0.523658   
6521                      Action|Sci-Fi|Thriller|IMAX      1.0    0.516437   
7866                      Action|Sci-Fi|Thriller|IMAX      1.0    0.510470   
4639            Action|Adventure|Sci-Fi|Thriller|IMAX      1.0    0.510384   
7562             Action|Drama|Mystery|Sci-Fi|Thriller      1.0    0.510372   
4351            Action|Adventure|Sci-Fi|Thriller|IMAX      1.0    0.507459   
8151                      Action|Sci-Fi|Thriller|IMAX      1.0    0.506846   

      genre_bias  prediction with genres bias  
7372       1.000                     0.517460  
6797       1.000                     0.513101  
3873       0.882                     0.463461  
8238       0.882                     0.461866  
6521       0.882                     0.455497  
7866       0.882                     0.450235  
4639       0.882                     0.450159  
7562       0.882                     0.450148  
4351       0.882                     0.447579  
8151       0.882                     0.447038

In [95]:
ratings = movies_not_watched.loc[:,'prediction']
ratings
highest_score = ratings[ratings.argsort()[-10:]][::-1]
highest_score

923    0.548188
896    0.481486
905    0.537141
914    0.543097
920    0.547119
906    0.553507
908    0.548492
900    0.541257
907    0.549986
922    0.531121
Name: prediction, dtype: float32

In [57]:
ratings_with_genre_bias[8000:8020]

8000    0.242123
8001    0.000000
8002    0.000000
8003    0.000000
8004    0.331919
8005    0.236291
8006    0.000000
8007    0.000000
8008    0.331483
8009    0.240243
8010    0.000000
8011    0.235045
8012    0.412072
8013    0.288372
8014    0.236949
8015    0.332894
8016    0.233025
8017    0.000000
8018    0.237433
8019    0.000000
Name: prediction with genres bias, dtype: float64

In [67]:
movies_not_watched_with_bias = movies_not_watched.sort_values(by=['prediction with genres bias'], ascending=False)
movies_not_watched_with_bias

index   movieId                                title  \
6797  6797.0   60684.0                      Watchmen (2009)   
7372  7372.0   79132.0                     Inception (2010)   
8533  8533.0  114935.0                Predestination (2014)   
6521  6521.0   53996.0                  Transformers (2007)   
6991  6991.0   67197.0                       Knowing (2009)   
...      ...       ...                                  ...   
3905  3905.0    5485.0                       Tadpole (2002)   
9741  9741.0  193609.0  Andrew Dice Clay: Dice Rules (1991)   
507      NaN       NaN                                  NaN   
7090     NaN       NaN                                  NaN   
8376     NaN       NaN                                  NaN   

                                               genres  fake_id  prediction  \
6797        Action|Drama|Mystery|Sci-Fi|Thriller|IMAX      1.0    0.524139   
7372  Action|Crime|Drama|Mystery|Sci-Fi|Thriller|IMAX      1.0    0.499663   
8533                   Action|Mystery|Sci-Fi|Thriller      1.0    0.515845   
6521                      Action|Sci-Fi|Thriller|IMAX      1.0    0.514928   
6991             Action|Drama|Mystery|Sci-Fi|Thriller      1.0    0.514395   
...                                               ...      ...         ...   
3905                             Comedy|Drama|Romance      1.0    0.513716   
9741                                           Comedy      1.0    0.499100   
507                                               NaN      NaN         NaN   
7090                                              NaN      NaN         NaN   
8376                                              NaN      NaN         NaN   

      genre_bias  prediction with genres bias  
6797       1.000                     0.524139  
7372       1.000                     0.499663  
8533       0.882                     0.454975  
6521       0.882                     0.454166  
6991       0.882                     0.453696  
...          ...                          ...  
3905       0.000                     0.000000  
9741       0.000                     0.000000  
507        0.578                          NaN  
7090       0.746                          NaN  
8376       0.578                          NaN  

[9742 rows x 8 columns]

In [70]:
movies_not_watched_with_bias[0:50]

index   movieId                                              title  \
6797  6797.0   60684.0                                    Watchmen (2009)   
7372  7372.0   79132.0                                   Inception (2010)   
8533  8533.0  114935.0                              Predestination (2014)   
6521  6521.0   53996.0                                Transformers (2007)   
6991  6991.0   67197.0                                     Knowing (2009)   
6470  6470.0   52722.0                                Spider-Man 3 (2007)   
8912  8912.0  135518.0                                   Self/less (2015)   
7562  7562.0   85414.0                                 Source Code (2011)   
5980  5980.0   36509.0                                   Cave, The (2005)   
8120  8120.0  101076.0                       G.I. Joe: Retaliation (2013)   
7625  7625.0   87306.0                                     Super 8 (2011)   
7508  7508.0   83613.0                            Cowboys & Aliens (2011)   
7545  7545.0   85056.0                            I Am Number Four (2011)   
4639  4639.0    6934.0                     Matrix Revolutions, The (2003)   
3873  3873.0    5445.0                             Minority Report (2002)   
5556  5556.0   26701.0  Patlabor: The Movie (Kidô keisatsu patorebâ: T...   
6664  6664.0   57368.0                                 Cloverfield (2008)   
4351  4351.0    6365.0                        Matrix Reloaded, The (2003)   
7324  7324.0   77561.0                                  Iron Man 2 (2010)   
7866  7866.0   94018.0                                  Battleship (2012)   
8151  8151.0  102125.0                                  Iron Man 3 (2013)   
9682  9682.0  183635.0                 Maze Runner: The Death Cure (2018)   
6145  6145.0   43932.0                                       Pulse (2006)   
6630  6630.0   56174.0                                 I Am Legend (2007)   
6151  6151.0   44191.0                              V for Vendetta (2006)   
1391  1391.0    1909.0              X-Files: Fight the Future, The (1998)   
7411  7411.0   80363.0                    Resident Evil: Afterlife (2010)   
963    963.0    1264.0                                        Diva (1981)   
5802  5802.0   31804.0                 Night Watch (Nochnoy dozor) (2004)   
8238  8238.0  104243.0                                     Riddick (2013)   
167    167.0     198.0                                Strange Days (1995)   
3052  3052.0    4086.0                               Big Easy, The (1987)   
7813  7813.0   92507.0                                  Safe House (2012)   
8278  8278.0  105653.0                                 Escape Plan (2013)   
7503  7503.0   83349.0                           Green Hornet, The (2011)   
7644  7644.0   88125.0  Harry Potter and the Deathly Hallows: Part 2 (...   
5539  5539.0   26614.0                        Bourne Identity, The (1988)   
1863  1863.0    2475.0                                  52 Pick-Up (1986)   
2413  2413.0    3204.0                       Boys from Brazil, The (1978)   
8849  8849.0  132618.0                                        Kite (2014)   
2354  2354.0    3113.0                                 End of Days (1999)   
5327  5327.0    8860.0                                    Cellular (2004)   
5167  5167.0    8369.0                                 Mindhunters (2004)   
3656  3656.0    5026.0  Brotherhood of the Wolf (Pacte des loups, Le) ...   
8103  8103.0  100498.0                     Good Day to Die Hard, A (2013)   
7260  7260.0   74510.0  Girl Who Played with Fire, The (Flickan som le...   
6995  6995.0   67361.0                          Echelon Conspiracy (2009)   
8379  8379.0  109578.0                                    Non-Stop (2014)   
8201  8201.0  103339.0                            White House Down (2013)   
7726  7726.0   90524.0                                   Abduction (2011)   

                                                 genres  fake_id  prediction  \

In [ ]:

a = x.argsort(), print x[a], we will get array([ 0.  ,  0.1 ,  1.41,  1.48]) – Belter Mar 12 '17 at 8:19


In [74]:
newhighscore = ratings_with_genre_bias[ratings_with_genre_bias.argsort()[-10:]][::-1]
newhighscore

#highest_score = ratings[ratings.argsort()[-10:]][::-1]
#ทำไมมันผิดแบบนี้วะ

6796    0.174329
7370    0.000000
8530    0.233969
6520    0.000000
6990    0.236451
6469    0.000000
8909    0.240230
7560    0.241866
5979    0.000000
8118    0.000000
Name: prediction with genres bias, dtype: float64

In [76]:
ratings_with_genre_bias.argsort()

0          0
1       5546
2       5545
3       5544
4       5543
        ... 
9737    6990
9738    6520
9739    8530
9740    7370
9741    6796
Name: prediction with genres bias, Length: 9742, dtype: int64

In [80]:
ratings_with_genre_bias.argsort()[-10:]

9732    8118
9733    5979
9734    7560
9735    8909
9736    6469
9737    6990
9738    6520
9739    8530
9740    7370
9741    6796
Name: prediction with genres bias, dtype: int64

In [ ]:
np.sort(array) == array[np.argsort(array)]

In [83]:
ratings_with_genre_bias

0       0.000000
1       0.000000
2       0.000000
3       0.000000
4       0.000000
          ...   
9737    0.231232
9738    0.000000
9739    0.000000
9740    0.229399
9741    0.000000
Name: prediction with genres bias, Length: 9742, dtype: float64

In [84]:
np.sort(ratings_with_genre_bias)

array([ 0.,  0.,  0., ..., nan, nan, nan])

In [85]:
ratings_with_genre_bias[np.argsort(ratings_with_genre_bias)]

KeyError: "Passing list-likes to .loc or [] with any missing labels is no longer supported. The following labels were missing: Int64Index([-1, -1, -1], dtype='int64'). See https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike"

In [ ]:
ทำไม argsort ยังไงให้ค่า 0.000000 อยู่ใน top 10 ได้วะ????



In [ ]:
all_movies.loc[all_movies['index'] == 9461]


In [40]:
movies_not_watched.loc[movies_not_watched['index'] == 7370]

index  movieId                       title       genres  fake_id  \
7370  7370.0  79073.0  When You're Strange (2009)  Documentary      1.0   

      prediction  genre_bias  prediction with genres bias  
7370    0.486437         0.0                          0.0

In [41]:
movies_not_watched.loc[movies_not_watched['index'] == 6796]

index  movieId                       title  genres  fake_id  \
6796  6796.0  60674.0  Stargate: Continuum (2008)  Sci-Fi      1.0   

      prediction  genre_bias  prediction with genres bias  
6796    0.474373       0.334                     0.158441

In [44]:
movies_not_watched.loc[movies_not_watched['index'] == 7543]

index  movieId             title  genres  fake_id  prediction  \
7543  7543.0  85022.0  Hall Pass (2011)  Comedy      1.0    0.503493   

      genre_bias  prediction with genres bias  
7543         0.0                          0.0

In [47]:
movies_not_watched.loc[movies_not_watched['index'] == 6629]

index  movieId                       title                      genres  \
6629  6629.0  56171.0  Golden Compass, The (2007)  Adventure|Children|Fantasy   

      fake_id  prediction  genre_bias  prediction with genres bias  
6629      1.0     0.49671         0.0                          0.0

In [42]:
movies_not_watched.loc[movies_not_watched['index'] == 7560]

index  movieId         title               genres  fake_id  prediction  \
7560  7560.0  85401.0  Super (2010)  Action|Comedy|Drama      1.0    0.489143   

      genre_bias  prediction with genres bias  
7560       0.471                     0.230386

In [43]:
movies_not_watched.loc[movies_not_watched['index'] == 167]

index  movieId                title  \
167  167.0    198.0  Strange Days (1995)   

                                         genres  fake_id  prediction  \
167  Action|Crime|Drama|Mystery|Sci-Fi|Thriller      1.0    0.497199   

     genre_bias  prediction with genres bias  
167       0.882                     0.438529

In [46]:
movies_not_watched.loc[movies_not_watched['index'] == 7864]

index  movieId                 title           genres  fake_id  \
7864  7864.0  94011.0  Big Bang, The (2011)  Action|Thriller      1.0   

      prediction  genre_bias  prediction with genres bias  
7864    0.495207       0.666                     0.329808

In [45]:
movies_not_watched.loc[movies_not_watched['index'] == 7409]

index  movieId           title                                  genres  \
7409  7409.0  80219.0  Machete (2010)  Action|Adventure|Comedy|Crime|Thriller   

      fake_id  prediction  genre_bias  prediction with genres bias  
7409      1.0    0.491917       0.666                     0.327617

In [52]:
movies_not_watched.loc[movies_not_watched['index'] == 6990]

index  movieId             title                  genres  fake_id  \
6990  6990.0  67193.0  Duplicity (2009)  Crime|Romance|Thriller      1.0   

      prediction  genre_bias  prediction with genres bias  
6990    0.507077       0.471                     0.238833

In [9]:
splittedgenres = [sub.split("|") for sub in allgenres]


In [15]:
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

def vect_cos(vect, test_list):

    """ Vectorise text and compute the cosine similarity """
    query_0 = vect.transform([' '.join(vect.get_feature_names())])
    query_1 = vect.transform(test_list)
    cos_sim = cosine_similarity(query_0.A, query_1.A)  # displays the resulting matrix
    return query_1, np.round(cos_sim.squeeze(), 3)

vectoriser3 = CountVectorizer().fit(vocab)
vectoriser3.vocabulary_ # show the word-matrix position pairs

{'action': 0, 'scifi': 3, 'mystery': 2, 'thriller': 4, 'imax': 1}

In [11]:
see = []
for item in splittedgenres[0]:
    perrow = item.lower()
    see.append(perrow)

In [12]:
see

['adventure', 'animation', 'children', 'comedy', 'fantasy']

In [13]:
see_vect, see_cos = vect_cos(vectoriser3, [' '.join(see)])
print('\nThe cosine similarity for the first list is {}.'.format(see_cos))


The cosine similarity for the first list is 0.0.


In [14]:
see2 = []
for item in splittedgenres[8856]:
    perrow = item.lower()
    see2.append(perrow)

In [15]:
see2

['comedy', 'crime', 'scifi']

In [26]:
see2_vect, see2_cos = vect_cos(vectoriser3, [' '.join(see2)])
print('\nThe cosine similarity for the second list is {}.'.format(see2_cos))


The cosine similarity for the second list is 0.447.


In [17]:
see2_vect, see2_cos

(<1x5 sparse matrix of type '<class 'numpy.int64'>'
 	with 1 stored elements in Compressed Sparse Row format>,
 0.447)

In [18]:
see_vect, see_cos

(<1x5 sparse matrix of type '<class 'numpy.int64'>'
 	with 0 stored elements in Compressed Sparse Row format>,
 0.0)

In [19]:
see2_vect

<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>

In [20]:
see2_cos

0.447

In [ ]:
#คือเรียกฟังชั่น vect_cos โดย parameter แรก คือ vectoriser3 ซึ่งคือโมเดลที่ฟิตไว้
#vectoriser3 = CountVectorizer().fit(vocab)
#เป็นเหมือนการทำไม้บรรทัดอะ คือ CountVectorizer นี่คือไม้บรรทัด แล้วต้องจับมาวัดทุกบรรทัด
#อันนั้นใช้ iterrow ก็ได้

#ส่วน parameter ตัวที่สอง คือ genre ของหนังแต่ละเรื่อง แต่ละบรรทัด
#ทีนี้ก็เอาไม้บรรทัดไปวัดทีละบรรทัด

In [ ]:
แต่ไม้บรรทัดมายังไงยังไม่ต้องรู้ก็ได้แมะ แค่จะเอาไม้บรรทัดไปวัด ทุกบรรทัด ทีละบรรทัด

In [31]:
for row in all_movies.iterrows():
    see = []
    for item in splittedgenres[0]:
        perrow = item.lower()
        see.append(perrow)
print(see)

['adventure', 'animation', 'children', 'comedy', 'fantasy']


In [32]:
all_movies.iterrows()

<generator object DataFrame.iterrows at 0x7f19a0d90350>

In [33]:
for i in all_movies.iterrows():
    print(i)

(0, index                                                0
movieId                                              1
title                                 Toy Story (1995)
genres     Adventure|Animation|Children|Comedy|Fantasy
Name: 0, dtype: object)
(1, index                               1
movieId                             2
title                  Jumanji (1995)
genres     Adventure|Children|Fantasy
Name: 1, dtype: object)
(2, index                            2
movieId                          3
title      Grumpier Old Men (1995)
genres              Comedy|Romance
Name: 2, dtype: object)
(3, index                             3
movieId                           4
title      Waiting to Exhale (1995)
genres         Comedy|Drama|Romance
Name: 3, dtype: object)
(4, index                                       4
movieId                                     5
title      Father of the Bride Part II (1995)
genres                                 Comedy
Name: 4, dtype: object)
(5, index           

Name: 173, dtype: object)
(174, index                  174
movieId                206
title      Unzipped (1995)
genres         Documentary
Name: 174, dtype: object)
(175, index                               175
movieId                             207
title      Walk in the Clouds, A (1995)
genres                    Drama|Romance
Name: 175, dtype: object)
(176, index                         176
movieId                       208
title           Waterworld (1995)
genres     Action|Adventure|SciFi
Name: 176, dtype: object)
(177, index                            177
movieId                          209
title      White Man's Burden (1995)
genres                         Drama
Name: 177, dtype: object)
(178, index                   178
movieId                 210
title      Wild Bill (1995)
genres              Western
Name: 178, dtype: object)
(179, index                               179
movieId                             211
title      Browning Version, The (1994)
genres                  

Name: 316, dtype: object)
(317, index                             317
movieId                           359
title      I Like It Like That (1994)
genres           Comedy|Drama|Romance
Name: 317, dtype: object)
(318, index                        318
movieId                      360
title      I Love Trouble (1994)
genres             Action|Comedy
Name: 318, dtype: object)
(319, index                                319
movieId                              361
title      It Could Happen to You (1994)
genres              Comedy|Drama|Romance
Name: 319, dtype: object)
(320, index                             320
movieId                           362
title         Jungle Book, The (1994)
genres     Adventure|Children|Romance
Name: 320, dtype: object)
(321, index                                                    321
movieId                                                  363
title      Wonderful, Horrible Life of Leni Riefenstahl, ...
genres                                           Document

Name: 456, dtype: object)
(457, index                        457
movieId                      522
title      Romper Stomper (1992)
genres              Action|Drama
Name: 457, dtype: object)
(458, index                          458
movieId                        523
title      Ruby in Paradise (1993)
genres                       Drama
Name: 458, dtype: object)
(459, index              459
movieId            524
title      Rudy (1993)
genres           Drama
Name: 459, dtype: object)
(460, index                                           460
movieId                                         526
title      Savage Nights (Nuits fauves, Les) (1992)
genres                                        Drama
Name: 460, dtype: object)
(461, index                          461
movieId                        527
title      Schindler's List (1993)
genres                   Drama|War
Name: 461, dtype: object)
(462, index                    462
movieId                  528
title      Scout, The (1994)
genres   

(584, index                      584
movieId                    719
title      Multiplicity (1996)
genres                  Comedy
Name: 584, dtype: object)
(585, index                                                    585
movieId                                                  720
title      Wallace & Gromit: The Best of Aardman Animatio...
genres                            Adventure|Animation|Comedy
Name: 585, dtype: object)
(586, index                                                  586
movieId                                                722
title      Haunted World of Edward D. Wood Jr., The (1996)
genres                                         Documentary
Name: 586, dtype: object)
(587, index                                587
movieId                              724
title                  Craft, The (1996)
genres     Drama|Fantasy|Horror|Thriller
Name: 587, dtype: object)
(588, index                               588
movieId                             725
title      Great W

...

Name: 9229, dtype: object)
(9230, index                      9230
movieId                  152284
title      War and Peace (2016)
genres            Drama|Romance
Name: 9230, dtype: object)
(9231, index                   9231
movieId               152372
title      Southbound (2016)
genres                Horror
Name: 9231, dtype: object)
(9232, index                 9232
movieId             152591
title      Ip Man 3 (2015)
genres              Action
Name: 9232, dtype: object)
(9233, index                              9233
movieId                          152658
title      Santa's Little Helper (2015)
genres                         Children
Name: 9233, dtype: object)
(9234, index                                9234
movieId                            152711
title      Who Killed Chea Vichea? (2010)
genres                        Documentary
Name: 9234, dtype: object)
(9235, index                                  9235
movieId                              152970
title      Hunt for the Wild

Name: 9350, dtype: object)
(9351, index                  9351
movieId              161044
title      Webmaster (1998)
genres                SciFi
Name: 9351, dtype: object)
(9352, index                        9352
movieId                    161127
title      The Infiltrator (2016)
genres                Crime|Drama
Name: 9352, dtype: object)
(9353, index                 9353
movieId             161131
title      War Dogs (2016)
genres              Comedy
Name: 9353, dtype: object)
(9354, index                          9354
movieId                      161290
title      Vigilante Diaries (2016)
genres                       Action
Name: 9354, dtype: object)
(9355, index                                 9355
movieId                             161354
title      Batman: The Killing Joke (2016)
genres        Action|Animation|Crime|Drama
Name: 9355, dtype: object)
(9356, index                 9356
movieId             161580
title      Bad Moms (2016)
genres              Comedy
Name: 9356, dtyp

Name: 9474, dtype: object)
(9475, index                                     9475
movieId                                 168632
title      Bill Burr: Walk Your Way Out (2017)
genres                                  Comedy
Name: 9475, dtype: object)
(9476, index                            9476
movieId                        168712
title      Fifty Shades Darker (2017)
genres                  Drama|Romance
Name: 9476, dtype: object)
(9477, index                             9477
movieId                         168846
title      Neal Brennan: 3 Mics (2017)
genres                          Comedy
Name: 9477, dtype: object)
(9478, index                 9478
movieId             169034
title      Lemonade (2016)
genres               (N/A)
Name: 9478, dtype: object)
(9479, index                       9479
movieId                   169180
title      American Fable (2017)
genres                  Thriller
Name: 9479, dtype: object)
(9480, index                 9480
movieId             169670
title 

Name: 9599, dtype: object)
(9600, index                      9600
movieId                  175781
title      Der Herr Karl (1961)
genres                   Comedy
Name: 9600, dtype: object)
(9601, index                                              9601
movieId                                          176051
title      LEGO DC Super Hero Girls: Brain Drain (2017)
genres                                        Animation
Name: 9601, dtype: object)
(9602, index                                    9602
movieId                                176101
title      Kingsman: The Golden Circle (2017)
genres                Action|Adventure|Comedy
Name: 9602, dtype: object)
(9603, index                                     9603
movieId                                 176329
title      Ari Shaffir: Double Negative (2017)
genres                                  Comedy
Name: 9603, dtype: object)
(9604, index                          9604
movieId                      176371
title      Blade Runner 2049 (2017

Name: 9735, dtype: object)
(9736, index                                          9736
movieId                                      193579
title      Jon Stewart Has Left the Building (2015)
genres                                  Documentary
Name: 9736, dtype: object)
(9737, index                                           9737
movieId                                       193581
title      Black Butler: Book of the Atlantic (2017)
genres               Action|Animation|Comedy|Fantasy
Name: 9737, dtype: object)
(9738, index                              9738
movieId                          193583
title      No Game No Life: Zero (2017)
genres         Animation|Comedy|Fantasy
Name: 9738, dtype: object)
(9739, index              9739
movieId          193585
title      Flint (2017)
genres            Drama
Name: 9739, dtype: object)
(9740, index                                     9740
movieId                                 193587
title      Bungo Stray Dogs: Dead Apple (2018)
genres       

In [34]:
for i in all_movies.iterrows():
    see = i
    see_vect, see_cos = vect_cos(vectoriser3, [' '.join(see)])
    print(see_cos)


TypeError: sequence item 0: expected str instance, int found

In [ ]:
values = ','.join(str(v) for v in value_list)

In [35]:
for i in all_movies.genres:
    see_cos = vect_cos(vectoriser3, [' '.join(i.iterrows())])
    print(see_cos)

AttributeError: 'str' object has no attribute 'iterrows'

In [36]:
for i in all_movies.genres:
    print(i)

Adventure|Animation|Children|Comedy|Fantasy
Adventure|Children|Fantasy
Comedy|Romance
Comedy|Drama|Romance
Comedy
Action|Crime|Thriller
Comedy|Romance
Adventure|Children
Action
Action|Adventure|Thriller
Comedy|Drama|Romance
Comedy|Horror
Adventure|Animation|Children
Drama
Action|Adventure|Romance
Crime|Drama
Drama|Romance
Comedy
Comedy
Action|Comedy|Crime|Drama|Thriller
Comedy|Crime|Thriller
Crime|Drama|Horror|Mystery|Thriller
Action|Crime|Thriller
Drama|SciFi
Drama|Romance
Drama
Children|Drama
Drama|Romance
Adventure|Drama|Fantasy|Mystery|SciFi
Crime|Drama
Drama
Mystery|SciFi|Thriller
Children|Drama
Crime|Drama
Children|Comedy
Comedy|Romance
Drama
Drama|War
Action|Crime|Drama
Drama
Action|Adventure|Fantasy
Comedy|Drama|Thriller
Drama|Romance
Mystery|Thriller
Animation|Children|Drama|Musical|Romance
Drama|Romance
Crime|Mystery|Thriller
Comedy|Drama|Romance
Adventure|Drama
Children|Comedy
Drama
Drama
Comedy|Drama|Romance
Adventure|Children|Fantasy
Drama|Thriller
Drama
Comedy|Crime
Comed

Drama
Comedy|Drama|War
Animation|Children|Fantasy|Musical
Drama|Western
Crime|FilmNoir|Mystery
Comedy
Drama|Romance
Action|Adventure|Drama
Comedy
Documentary
Drama|Romance
Action|Adventure
Comedy|Drama
Drama
Drama
Drama|Romance
Comedy
Drama|Musical
Drama|War
Comedy|Drama
Drama|SciFi
Children|Drama|Fantasy
Adventure|Drama
Action|Western
Drama|Romance
Adventure|Drama|SciFi
Comedy|Romance
Documentary
Drama
Comedy|Drama
Action|Horror|SciFi|Thriller
Comedy|Horror|Thriller
Horror
Horror
Horror
Horror
Horror
Drama|Horror|Mystery|Thriller
Horror
Horror
Horror
Horror
Horror|Thriller
Horror|Thriller
Horror|SciFi
Horror|Mystery
Horror|Thriller
Drama|Horror|Thriller
Fantasy|Horror|Romance|Thriller
Drama|Horror|SciFi
Horror
Horror|Thriller
Thriller
Crime|Drama|Thriller
Drama|Fantasy|Horror|Thriller
Drama|Fantasy|Horror
Horror|Thriller
Horror
Horror
Horror|Mystery|Thriller
Crime|Drama|Thriller
Crime|Thriller
Comedy|Drama|Romance
Drama|Mystery
Horror|Thriller
Action|Adventure|SciFi|Thriller
Drama|Rom

Action|SciFi|Thriller
Crime|Thriller
Comedy|Horror
Drama|Romance
Drama
Drama
Drama|FilmNoir
Comedy|Horror|SciFi
Action|Horror|SciFi
Adventure|SciFi
Action|Crime
Action|Adventure|Comedy|Fantasy|Horror|Thriller
Comedy
Drama|Romance
Comedy|Fantasy
Comedy
Drama|Fantasy
Action|Adventure|Crime|SciFi|Thriller
Action|Adventure|SciFi
Comedy|Romance
Drama
Adventure|Drama|Mystery
Horror|Romance
Horror
Drama
Action|Adventure|SciFi
Action|SciFi
Action|Adventure|SciFi
Action|Adventure|SciFi
Horror
Drama|Horror|SciFi
Horror
Horror
Drama|Fantasy|Horror
Horror
Horror|SciFi
Comedy|Horror|Musical|SciFi
Comedy|Documentary
Horror|SciFi
SciFi
Action|Drama|SciFi
Horror|SciFi|Thriller
SciFi
Horror|SciFi
War
War
Comedy|Romance
Drama|SciFi|Thriller
Drama|Fantasy
Drama|Thriller
Documentary|Musical
Comedy|Romance|SciFi
Drama
Action|Adventure|Comedy
Drama|Mystery
Adventure|Animation|Children|Drama
Crime|Drama|Mystery|Thriller
Comedy|Romance
Drama
Action|Crime
Documentary
Comedy
Drama
Comedy
Comedy|Drama|Romance
Sc

Drama
Drama
Drama
Horror
Horror
Horror
Drama|Fantasy|Mystery|Romance
Comedy
Comedy|Drama
Adventure|SciFi
Adventure|SciFi
Comedy|Horror
Comedy
Adventure|Horror|SciFi
Horror|SciFi
Horror|SciFi
SciFi|Thriller
Horror
Horror
Horror
Horror
Horror
Comedy
Adventure|Animation|Children
Action|Drama|Thriller
Action|Crime|Drama|Thriller
Comedy
Drama
Drama
Drama
Drama|Thriller
Comedy|Romance
Comedy
Action|Drama
Drama
Action|Adventure|SciFi
Comedy|Horror
Musical
Animation|Children
Drama|FilmNoir
Crime|FilmNoir
Drama
Comedy
Drama
Comedy|Mystery
Action|Comedy
Crime|Horror|Mystery|Thriller
Adventure|Children
Action|Comedy
Drama|Romance
Comedy
Drama
Action|SciFi|Thriller
Drama|Romance
Action|Adventure|Thriller
Drama|War
Action|SciFi|Thriller
Drama|Romance
Children|Comedy|Fantasy
Documentary
Animation|Children|Comedy
Children|Comedy
Drama|Romance|War
Drama|Romance
Drama|SciFi
Action|Drama|Romance
Action|Adventure|Comedy|Fantasy
Drama
Action|Adventure
Adventure|Drama
Comedy
Comedy
Action|Adventure|Thrille

Comedy|Drama
Comedy|Drama|Thriller
Drama|Fantasy
Action|Mystery|Thriller
Adventure|Children|Comedy|Fantasy|Mystery
Action|Drama|War
Drama
Comedy
Action|Crime|Thriller
Crime|Drama|Romance|Thriller
Drama|War
Comedy
Comedy
Adventure|Drama|Horror|Mystery|Thriller
Drama|FilmNoir|Thriller
Western
Comedy|SciFi|Thriller
Action|Comedy
Western
Action|Comedy|Crime
Comedy
Adventure|Animation|Children|SciFi
Action|Crime|Mystery|SciFi|Thriller
Adventure|Drama
Drama
Adventure|Animation|Children|Comedy
Comedy|Romance
Comedy|Drama|Romance
Comedy|Drama|Romance
Children|Comedy|Romance
Comedy|Romance
Comedy|Drama
Comedy|Western
Children|Comedy|Fantasy
Action|Comedy|SciFi
Action|Animation|Children|Comedy
Comedy|Drama
Adventure|Comedy
Action|Adventure|Fantasy
Crime|Drama
Crime|Drama|Thriller
Comedy|Drama|Romance
SciFi
Comedy|Romance
Drama|Romance
Children|Drama|Musical
Drama|Mystery|Thriller
Horror|Thriller
Drama|Romance
Action|Comedy|Horror|SciFi
Action|Adventure|Drama|Thriller
Children|Comedy
Comedy
Docum

Drama
Drama|SciFi|Thriller
Comedy|Romance
Adventure|Documentary
Comedy|Crime|Thriller
Comedy|Crime
Drama|Musical
Comedy|Drama|Romance
Comedy
Action|Adventure|Children|Comedy|Crime
Drama
Comedy|Romance
Drama
Comedy|Horror|SciFi
Comedy|Horror|Thriller
Drama
Comedy|War
Comedy|Romance
Comedy
Comedy|Drama
Drama
Drama
Action|Adventure|Fantasy
Drama|War
Animation|Comedy|Fantasy|Musical
Crime|Drama|Mystery|Thriller
Comedy|Crime|Mystery
Action|Adventure|Drama|War
Adventure|Comedy
Action
Drama|Romance
Comedy|Drama
Comedy|Drama
Comedy
Adventure|Comedy
Drama
Comedy|Horror
Romance
Thriller
Comedy|Drama
Adventure|Drama
Action|Comedy|Crime|Thriller
Crime|Drama
Drama
Drama
Crime|Drama|Thriller
FilmNoir
Drama|War
Comedy
Comedy|Crime
Action|Adventure|Children|Comedy
Comedy|Romance
Mystery|Thriller
Thriller
Drama
Comedy|Drama|Romance
Comedy|Drama|Romance
Drama|Romance
Action|Drama|Horror|Thriller
Drama|Romance|SciFi
Crime|Drama|Thriller
Comedy|Crime|Drama
Comedy|Drama|Romance
Comedy|Crime
Crime|Drama|Thr

Action|Animation|Drama|SciFi
Action|Comedy|Romance
Comedy|Romance
Comedy
Comedy|Musical|Romance
Action|Fantasy|Horror|Thriller
Adventure|Children|Comedy|Fantasy
Children|Comedy|Drama
Drama|War
Mystery|Thriller
Action|Fantasy|Horror|Mystery|SciFi|Thriller
Comedy
Action|Comedy
Action|Comedy
Drama|Romance
Comedy|Horror
Adventure|Comedy|Crime|Drama|Mystery|Thriller
Action|Adventure|Comedy
Adventure|Comedy|Romance
Comedy|Crime|Drama|Mystery
Drama|War
Comedy|Drama|Romance
Horror|Thriller
Action|Comedy
Comedy|Crime|Musical
Documentary|War
Action|Crime|Drama|Thriller
Adventure|Animation|Children|Comedy|Fantasy|SciFi|IMAX
Drama
Horror|Mystery
Comedy
Drama
Comedy
Crime|Drama|Thriller
Horror|Mystery|SciFi|Thriller
Drama
Action|Comedy|Crime
Children|Comedy|Drama
Comedy|Drama
Drama
Adventure|Comedy|Crime
Comedy|Romance
Action|Comedy
Documentary
Adventure|Comedy|Documentary
Crime|Drama|FilmNoir
Action|Drama
Comedy|Crime|Drama|Western
Action|Comedy
Comedy
Animation|Comedy|Drama|Fantasy
Action|Comedy|

Documentary
Drama|Romance
Documentary
Comedy|Drama
Drama
Horror|Thriller
Drama|Fantasy|Romance
Drama|Horror|Musical|Thriller
Action|Adventure
Drama|Western
Comedy|Drama|War
Action|Horror|SciFi
Comedy|Musical
Comedy|Drama|Romance
Comedy
Comedy|Drama|Romance
Adventure|Children|Fantasy
Action|Drama|SciFi|Thriller
Comedy|Drama|Romance
Comedy|Romance
Crime|Drama|Thriller
Drama
Comedy|Drama
Drama|Horror|Thriller
Action|Adventure|Fantasy
Action|Mystery|SciFi|Thriller
Comedy|Horror
Action|Adventure|Drama|War
Adventure|Animation|Drama|Horror
Animation|Comedy|Drama|Romance|SciFi
Comedy|Crime
Crime|Thriller
Action|Drama|Thriller|War
Comedy
Comedy
Horror|SciFi|Thriller
Action|Adventure|Fantasy|SciFi
Comedy|Crime|Drama|Thriller
Crime|SciFi
Action|Crime|Drama
Comedy|Horror
Action|Adventure|Comedy|Romance
Action|Adventure|Drama|SciFi|Thriller
Comedy|Drama|Romance
Crime|Drama|Romance|Thriller
Action|Drama|Thriller
Adventure|Children|Drama|Fantasy|IMAX
Drama|Musical|Romance
Drama|Romance
Comedy
Comedy|

Action|Adventure|Drama
Documentary
Comedy|Romance
Comedy|Drama|Romance
Action|Adventure|Fantasy|IMAX
Drama
Action|Comedy|SciFi
Horror
Comedy
Action|Crime
Comedy|Horror|SciFi|Thriller
Comedy|Drama
Comedy
Mystery|Thriller
Drama|Romance
Action|Thriller
Adventure|Comedy|Fantasy
Action|SciFi|Thriller|IMAX
Comedy|Drama
Documentary
Documentary
Comedy|Romance
Action|Animation|Fantasy
SciFi|Thriller
Comedy|Romance
Comedy
Drama
Action|Crime|Thriller
Comedy|Horror|IMAX
Drama|Thriller
Comedy|Romance
Comedy|Drama
Comedy
Documentary
Action|Comedy|SciFi|IMAX
Action|Adventure|Drama
Drama|Mystery|SciFi
Drama|Fantasy|SciFi
Adventure|Animation|Children|Comedy
Action|Horror|SciFi|IMAX
Horror|Mystery|Thriller
Comedy|Crime|Drama
Drama|Thriller
Drama|Romance
Comedy
Comedy|Drama|Romance
Action|Crime|Drama|Thriller
Action|Animation
Comedy|Drama
Comedy|Drama
Adventure|Animation|Children|Comedy|IMAX
Comedy|Drama
Action|Adventure|Animation|Children
Action|Adventure|Animation|Children
Action|Animation|Fantasy
Acti

Comedy
Drama|Romance
Drama
Drama
Comedy
Drama|Thriller
Adventure|Comedy|Drama
Drama|Mystery|Thriller
Documentary
Documentary
Documentary
Documentary
Documentary
Drama
Comedy
Comedy|Drama
Drama
Comedy
Drama|Thriller
Comedy|Drama
Thriller
Action|Adventure|SciFi|Thriller
Animation|Comedy
Comedy|Western
Comedy
Comedy
Comedy
Comedy|Romance
Western
Comedy
Action|Crime|Drama|Thriller
Drama|Mystery|Romance
Comedy
Action|Horror|SciFi
Mystery|Thriller
Comedy|Drama|Romance
Crime|Drama|Romance
Western
Drama
Comedy|Drama|Musical|Romance
Horror
Action|Adventure|Fantasy
Comedy
Documentary
Documentary
Adventure|Comedy|Drama
Comedy
Action|Adventure|Children|Comedy|SciFi
Animation|Children|Comedy
Comedy|SciFi
Animation|Comedy|SciFi
Comedy
Action|Adventure
(N/A)
Comedy
Horror|Thriller
Comedy|Crime|Drama|Romance
Action|Fantasy|SciFi
Comedy|Drama
Comedy
Action
Drama
Comedy
Action|Animation|SciFi
Action|Crime|Drama|Thriller
Drama|Fantasy|Horror|Mystery|Thriller
Drama|Horror
Children|Drama|Fantasy|Romance
Ac

In [37]:
splitted2 = [sub2.split("|") for sub2 in i]
genre_list = []
for sublist in splitted2:
    for item in sublist:
        genre_list.append(item)
genre_list

['C', 'o', 'm', 'e', 'd', 'y']

In [38]:
i #ขำเลย ไปนอนล่ะ

'Comedy'

In [ ]:
splitted2 = [sub2.split("|") for sub2 in i]


In [39]:
i

'Comedy'

In [43]:
for i in all_movies.genres:
    i_splitted = i.split("|")
    print(i_splitted)

['Adventure', 'Animation', 'Children', 'Comedy', 'Fantasy']
['Adventure', 'Children', 'Fantasy']
['Comedy', 'Romance']
['Comedy', 'Drama', 'Romance']
['Comedy']
['Action', 'Crime', 'Thriller']
['Comedy', 'Romance']
['Adventure', 'Children']
['Action']
['Action', 'Adventure', 'Thriller']
['Comedy', 'Drama', 'Romance']
['Comedy', 'Horror']
['Adventure', 'Animation', 'Children']
['Drama']
['Action', 'Adventure', 'Romance']
['Crime', 'Drama']
['Drama', 'Romance']
['Comedy']
['Comedy']
['Action', 'Comedy', 'Crime', 'Drama', 'Thriller']
['Comedy', 'Crime', 'Thriller']
['Crime', 'Drama', 'Horror', 'Mystery', 'Thriller']
['Action', 'Crime', 'Thriller']
['Drama', 'SciFi']
['Drama', 'Romance']
['Drama']
['Children', 'Drama']
['Drama', 'Romance']
['Adventure', 'Drama', 'Fantasy', 'Mystery', 'SciFi']
['Crime', 'Drama']
['Drama']
['Mystery', 'SciFi', 'Thriller']
['Children', 'Drama']
['Crime', 'Drama']
['Children', 'Comedy']
['Comedy', 'Romance']
['Drama']
['Drama', 'War']
['Action', 'Crime', 'Dram

['Drama', 'War']
['Action', 'Drama', 'Mystery', 'Romance', 'Thriller']
['Comedy', 'Fantasy', 'Romance']
['Drama', 'Western']
['Crime', 'Thriller', 'War']
['Comedy', 'Drama']
['Comedy', 'Mystery', 'Thriller']
['Adventure', 'Comedy', 'SciFi']
['Comedy', 'Crime', 'Drama']
['Drama', 'War']
['Comedy', 'Drama', 'FilmNoir']
['Action', 'Adventure', 'Animation', 'SciFi']
['Action', 'Adventure', 'Fantasy']
['Drama']
['Comedy', 'Drama', 'Romance']
['Comedy', 'Fantasy']
['Comedy', 'Drama']
['Drama']
['Comedy', 'Drama', 'War']
['Animation', 'Children', 'Fantasy', 'Musical']
['Drama', 'Western']
['Crime', 'FilmNoir', 'Mystery']
['Comedy']
['Drama', 'Romance']
['Action', 'Adventure', 'Drama']
['Comedy']
['Documentary']
['Drama', 'Romance']
['Action', 'Adventure']
['Comedy', 'Drama']
['Drama']
['Drama']
['Drama', 'Romance']
['Comedy']
['Drama', 'Musical']
['Drama', 'War']
['Comedy', 'Drama']
['Drama', 'SciFi']
['Children', 'Drama', 'Fantasy']
['Adventure', 'Drama']
['Action', 'Western']
['Drama', 'Rom

['Drama']
['Comedy']
['Adventure', 'Animation', 'Children', 'Drama', 'SciFi']
['Drama', 'Horror', 'Mystery']
['Action', 'Mystery']
['Crime', 'Drama', 'Romance', 'Thriller']
['Comedy', 'Drama']
['Comedy', 'Drama']
['Crime', 'Drama']
['Comedy']
['Drama']
['Comedy']
['Comedy', 'Romance']
['Drama']
['Comedy']
['Horror']
['Horror']
['Comedy']
['Horror']
['Comedy']
['Horror']
['Horror', 'Thriller']
['Comedy']
['Comedy']
['Comedy', 'Horror', 'Romance', 'Thriller']
['Adventure', 'Comedy', 'Romance']
['Comedy']
['Comedy']
['Comedy', 'Drama', 'Fantasy', 'Romance']
['Children', 'Comedy']
['Comedy']
['Adventure', 'Animation', 'Children', 'Drama', 'Fantasy']
['Drama', 'Romance']
['Action', 'Drama', 'Romance', 'Thriller']
['Crime', 'Drama', 'Mystery', 'Romance', 'Thriller']
['Children', 'Comedy']
['Comedy', 'Romance']
['Comedy', 'Thriller']
['Action', 'SciFi']
['Action', 'SciFi']
['Animation', 'Horror', 'Mystery', 'Thriller']
['Action', 'Thriller']
['Documentary']
['Action', 'War']
['Action', 'War']

['Comedy', 'Drama', 'Romance']
['Drama', 'Fantasy']
['Comedy']
['Comedy', 'Romance']
['Comedy', 'Drama']
['Comedy', 'Drama', 'Musical']
['Comedy', 'Crime']
['Drama']
['Comedy']
['Children', 'Fantasy', 'Musical']
['Drama', 'Romance']
['Drama']
['Crime', 'FilmNoir', 'Thriller']
['Action', 'Comedy', 'Romance']
['Drama']
['Documentary']
['Romance', 'Thriller']
['Adventure', 'Animation', 'Children', 'Comedy', 'Fantasy', 'Romance']
['Comedy', 'Romance']
['Drama', 'Musical', 'Romance']
['Action', 'Drama', 'Romance', 'War']
['Adventure', 'Drama']
['Drama']
['Drama']
['Comedy', 'Romance']
['Comedy', 'Western']
['Drama']
['Adventure', 'War', 'Western']
['Drama']
['Crime', 'Drama', 'Thriller']
['Adventure', 'Western']
['Western']
['Comedy', 'Crime']
['Drama']
['Drama', 'Romance', 'War']
['Drama', 'War']
['Action', 'Adventure', 'Drama', 'War']
['Comedy']
['Drama', 'Romance']
['Comedy', 'SciFi']
['Action', 'Crime', 'Drama']
['Drama']
['Comedy', 'Drama']
['Comedy', 'War']
['Comedy', 'Documentary']
[

['Drama', 'Mystery']
['Drama', 'Romance']
['Comedy', 'Drama', 'Romance']
['Comedy']
['Comedy']
['Action', 'Comedy']
['Comedy']
['Action', 'Drama', 'Thriller']
['Crime', 'Drama', 'Mystery', 'Thriller']
['Drama']
['Drama']
['Drama']
['Comedy', 'Drama', 'Romance']
['Action', 'Drama', 'Thriller']
['Drama', 'Horror', 'Thriller']
['Drama']
['Comedy', 'Crime', 'Drama']
['Drama']
['Comedy', 'Romance', 'Thriller']
['Adventure', 'Children', 'Drama']
['Drama', 'Mystery']
['Drama', 'War']
['Drama']
['Comedy', 'Drama', 'Romance']
['Adventure', 'Children', 'SciFi']
['Comedy', 'Drama', 'Romance']
['Horror', 'Mystery', 'Thriller']
['Drama']
['Comedy', 'Drama', 'Musical', 'Romance']
['Drama']
['Comedy']
['Drama', 'Horror', 'SciFi', 'Thriller']
['Animation', 'Children']
['Comedy', 'Romance']
['Comedy', 'Romance']
['Drama', 'Thriller', 'War']
['Action', 'Drama', 'SciFi', 'Thriller']
['Comedy']
['Comedy', 'Drama', 'Romance']
['Drama', 'Thriller']
['Comedy', 'Drama', 'Romance']
['Documentary']
['Drama', 'F

['Action', 'Adventure', 'Drama']
['Drama', 'Romance']
['Drama', 'Thriller']
['Drama', 'Romance', 'Thriller']
['Drama', 'Romance']
['Drama']
['Drama']
['Drama']
['Action', 'Crime', 'Drama', 'Mystery', 'Thriller']
['Action', 'Horror', 'SciFi', 'Thriller']
['Comedy', 'Drama']
['Action', 'Adventure', 'SciFi']
['Comedy', 'Romance']
['Comedy', 'Romance']
['Drama', 'Mystery', 'SciFi', 'Thriller']
['Adventure', 'Drama']
['Comedy', 'Horror']
['Drama']
['Crime', 'Mystery', 'Thriller']
['Drama']
['Action', 'Drama', 'Horror', 'Thriller']
['Adventure', 'Drama']
['Horror']
['Animation', 'Children', 'Comedy']
['Action', 'Drama', 'Thriller']
['Comedy']
['Romance']
['Action', 'Comedy']
['Drama', 'SciFi']
['Drama']
['Comedy', 'Romance']
['Action', 'Adventure', 'Animation', 'Comedy']
['Comedy', 'Crime', 'Drama']
['Comedy', 'Drama', 'Fantasy', 'Romance']
['Drama']
['Drama', 'Romance']
['Comedy', 'Horror']
['Comedy', 'Drama']
['Animation', 'Children', 'Comedy']
['Action', 'Drama']
['Documentary']
['SciFi',

['Drama', 'Romance']
['Drama']
['Drama', 'Thriller']
['Drama', 'Musical']
['Drama']
['Documentary']
['Drama', 'Mystery', 'Thriller']
['Comedy', 'Drama']
['Drama']
['Action', 'Adventure']
['Action', 'Drama']
['Drama', 'Mystery', 'Thriller']
['Drama', 'War']
['Action', 'Horror', 'Thriller']
['Drama', 'Musical']
['Drama']
['Comedy', 'Romance']
['Drama', 'Romance']
['Comedy']
['Comedy']
['Horror', 'Thriller']
['Crime', 'Drama']
['Action', 'Horror', 'Thriller']
['Drama']
['Adventure', 'Children', 'Fantasy']
['Comedy']
['Horror']
['Documentary']
['Comedy', 'Drama', 'Romance']
['Documentary']
['Comedy', 'Drama', 'Romance']
['Action', 'Crime', 'Drama', 'Thriller']
['Drama', 'Fantasy', 'Horror', 'Romance']
['Adventure', 'Comedy']
['Drama', 'Horror', 'Thriller']
['Comedy', 'Drama', 'Romance']
['Drama', 'Horror', 'Thriller']
['Comedy', 'Romance']
['Comedy', 'Drama']
['Documentary']
['Animation', 'Children', 'Drama']
['Romance']
['Drama']
['Comedy']
['Comedy', 'Romance']
['Animation', 'Comedy']
['

['Drama', 'Fantasy', 'Romance', 'SciFi']
['Comedy']
['Crime', 'Drama', 'Thriller']
['Crime']
['Action']
['Children', 'Comedy']
['Comedy', 'Romance']
['Action', 'Comedy']
['Crime', 'Documentary']
['Comedy', 'Drama']
['Action', 'Adventure', 'Thriller']
['Action', 'Comedy', 'Fantasy', 'Musical', 'Romance']
['Drama']
['Fantasy', 'Horror', 'Mystery', 'Thriller']
['Action', 'Horror', 'Thriller']
['Action', 'Adventure', 'Fantasy', 'Mystery']
['Comedy', 'Drama', 'Mystery']
['Comedy', 'Drama']
['Action', 'Adventure', 'Animation', 'Fantasy', 'SciFi']
['Horror', 'Thriller']
['Action', 'Crime', 'Drama']
['Drama', 'Thriller']
['Comedy', 'Documentary']
['Action', 'Horror', 'Thriller']
['Comedy', 'Romance']
['Action', 'Adventure', 'Comedy', 'Crime', 'Thriller']
['Comedy', 'Romance']
['Action', 'Horror', 'SciFi', 'Thriller', 'IMAX']
['Drama']
['Drama']
['Documentary', 'Drama', 'Mystery']
['Crime', 'Drama', 'Thriller']
['Comedy', 'Romance']
['Drama', 'Romance']
['Drama']
['Comedy', 'Drama']
['Comedy', 

['Comedy', 'Drama']
['Horror']
['Drama']
['Drama', 'Thriller']
['Adventure', 'Animation', 'Children', 'Comedy']
['Comedy', 'Documentary']
['Comedy']
['Drama', 'SciFi', 'IMAX']
['Comedy', 'Horror']
['Comedy', 'Romance']
['Comedy', 'Horror']
['Action', 'Animation', 'Children', 'Comedy', 'Musical']
['Action', 'Crime', 'Drama']
['Drama']
['Comedy']
['Action', 'Adventure', 'Animation', 'Children', 'Comedy']
['Comedy']
['Action', 'SciFi']
['Action', 'Adventure', 'SciFi']
['Action', 'Adventure', 'SciFi', 'IMAX']
['Comedy']
['Thriller']
['Comedy']
['Horror', 'SciFi', 'Thriller']
['Comedy']
['Comedy', 'Romance']
['Action', 'Adventure', 'Children', 'IMAX']
['Action', 'Comedy', 'Horror']
['Comedy', 'Romance']
['Drama', 'Fantasy']
['Comedy', 'Western']
['Action', 'SciFi', 'IMAX']
['Action', 'Adventure', 'Thriller']
['Action', 'Adventure', 'Fantasy']
['Comedy', 'Drama']
['Comedy']
['Drama']
['Action', 'Drama']
['Drama']
['Drama', 'Romance']
['Action', 'Animation', 'Children']
['Drama']
['Action', '

['Comedy', 'Drama']
['Horror']
['(N/A)']
['Comedy']
['Documentary']
['Comedy', 'Drama']
['Action', 'Animation', 'Comedy']
['Animation', 'Comedy']
['Children', 'Comedy', 'Drama']
['Comedy']
['Action', 'Adventure', 'Fantasy', 'SciFi']
['Animation', 'Fantasy', 'Mystery']
['Comedy']
['Comedy']
['Animation', 'Fantasy', 'Mystery']
['Action', 'Crime', 'Thriller']
['Horror']
['Action', 'SciFi']
['Action', 'Adventure', 'Fantasy']
['Crime', 'Drama']
['Comedy', 'Romance']
['Drama']
['SciFi', 'Thriller']
['Fantasy', 'Romance']
['Animation', 'Children', 'Comedy']
['Action', 'Adventure', 'Drama']
['Drama', 'Romance']
['Drama']
['Action', 'Drama', 'SciFi']
['Comedy']
['Drama', 'Romance']
['Comedy']
['(N/A)']
['Thriller']
['Horror']
['SciFi']
['Comedy']
['Drama', 'Mystery']
['Action', 'Adventure', 'SciFi']
['Action', 'Horror', 'SciFi', 'Thriller']
['Action', 'Crime', 'Drama']
['Action', 'Horror', 'SciFi']
['Action', 'Animation', 'SciFi']
['Drama', 'Mystery', 'Romance']
['Comedy']
['Action', 'Comedy', 

In [46]:
for i in all_movies.genres:
    i_splitted = i.split("|")
    genre = [genre.lower() for genre in i_splitted]

    print(genre)

['adventure', 'animation', 'children', 'comedy', 'fantasy']
['adventure', 'children', 'fantasy']
['comedy', 'romance']
['comedy', 'drama', 'romance']
['comedy']
['action', 'crime', 'thriller']
['comedy', 'romance']
['adventure', 'children']
['action']
['action', 'adventure', 'thriller']
['comedy', 'drama', 'romance']
['comedy', 'horror']
['adventure', 'animation', 'children']
['drama']
['action', 'adventure', 'romance']
['crime', 'drama']
['drama', 'romance']
['comedy']
['comedy']
['action', 'comedy', 'crime', 'drama', 'thriller']
['comedy', 'crime', 'thriller']
['crime', 'drama', 'horror', 'mystery', 'thriller']
['action', 'crime', 'thriller']
['drama', 'scifi']
['drama', 'romance']
['drama']
['children', 'drama']
['drama', 'romance']
['adventure', 'drama', 'fantasy', 'mystery', 'scifi']
['crime', 'drama']
['drama']
['mystery', 'scifi', 'thriller']
['children', 'drama']
['crime', 'drama']
['children', 'comedy']
['comedy', 'romance']
['drama']
['drama', 'war']
['action', 'crime', 'dram

['drama']
['drama']
['drama']
['comedy', 'romance']
['documentary']
['crime', 'drama', 'romance']
['documentary', 'musical']
['documentary']
['drama']
['comedy']
['action', 'adventure', 'scifi']
['action', 'adventure', 'comedy', 'fantasy', 'romance']
['action', 'adventure']
['fantasy', 'scifi']
['action', 'adventure', 'horror', 'scifi']
['action', 'adventure', 'western']
['comedy']
['drama']
['adventure', 'drama', 'war']
['crime', 'drama', 'scifi', 'thriller']
['drama']
['action', 'drama', 'war']
['action', 'drama', 'western']
['action', 'adventure', 'scifi']
['drama', 'fantasy', 'romance']
['filmnoir', 'mystery', 'thriller']
['crime', 'drama']
['horror', 'scifi']
['action', 'adventure', 'comedy', 'fantasy', 'horror']
['adventure', 'drama', 'romance']
['drama', 'war']
['action', 'crime', 'drama', 'thriller']
['crime', 'horror']
['action', 'comedy', 'musical']
['crime', 'drama']
['drama', 'war']
['adventure', 'animation', 'children', 'comedy', 'scifi']
['action', 'drama', 'romance', 'wa

['comedy']
['drama']
['drama']
['horror', 'mystery', 'thriller']
['comedy', 'romance']
['romance']
['comedy', 'drama']
['action', 'adventure', 'drama', 'thriller']
['mystery', 'scifi', 'thriller']
['drama']
['drama']
['comedy', 'thriller']
['comedy']
['drama']
['comedy', 'drama']
['action', 'thriller']
['animation', 'children', 'comedy']
['adventure', 'animation', 'children', 'comedy']
['comedy']
['drama']
['drama', 'war']
['comedy']
['drama']
['comedy']
['drama']
['drama', 'horror', 'scifi']
['action', 'horror', 'scifi', 'thriller']
['action', 'scifi']
['action', 'adventure', 'fantasy', 'horror']
['adventure', 'fantasy', 'romance', 'scifi', 'thriller']
['adventure', 'scifi']
['comedy', 'drama', 'romance']
['action', 'adventure', 'drama']
['comedy', 'crime', 'mystery']
['comedy']
['action', 'adventure', 'fantasy']
['comedy', 'drama']
['comedy']
['action', 'adventure', 'thriller']
['horror', 'scifi']
['comedy', 'crime']
['comedy', 'crime']
['comedy', 'crime']
['comedy', 'crime']
['comed

['drama']
['crime', 'horror', 'mystery', 'thriller']
['comedy', 'drama', 'romance']
['comedy', 'drama']
['comedy']
['documentary']
['comedy', 'drama']
['comedy']
['drama', 'musical']
['drama', 'horror', 'thriller']
['comedy', 'drama']
['comedy', 'musical', 'romance']
['horror']
['crime', 'drama', 'thriller']
['comedy']
['drama', 'thriller']
['drama', 'romance']
['action', 'thriller', 'war']
['drama', 'romance']
['mystery', 'thriller']
['comedy', 'drama', 'romance']
['action', 'horror']
['children', 'comedy']
['comedy', 'drama']
['comedy', 'drama']
['comedy', 'drama', 'romance']
['comedy', 'romance']
['comedy', 'drama']
['comedy', 'drama']
['horror', 'scifi']
['horror', 'scifi']
['horror', 'scifi']
['action', 'horror', 'scifi']
['drama', 'romance']
['action', 'adventure', 'drama']
['drama']
['comedy']
['action', 'drama', 'romance', 'thriller']
['drama', 'romance']
['horror']
['comedy', 'drama']
['comedy', 'drama']
['animation', 'scifi']
['action', 'scifi']
['drama', 'musical']
['comedy'

['children', 'comedy']
['comedy', 'romance']
['comedy', 'drama']
['action', 'adventure', 'drama', 'war']
['horror']
['comedy', 'romance']
['crime', 'drama']
['comedy', 'musical']
['horror', 'mystery', 'thriller']
['drama']
['drama', 'romance']
['drama', 'romance']
['comedy', 'crime', 'romance']
['comedy', 'crime']
['action', 'comedy']
['drama']
['crime', 'drama', 'filmnoir', 'mystery', 'thriller']
['comedy', 'drama']
['action', 'animation', 'scifi']
['horror']
['action', 'crime', 'thriller']
['drama', 'musical']
['comedy']
['drama']
['comedy', 'crime']
['documentary', 'imax']
['crime', 'horror', 'mystery', 'thriller']
['action']
['comedy', 'drama']
['drama']
['animation', 'drama', 'fantasy']
['drama', 'fantasy', 'mystery', 'scifi']
['horror', 'thriller']
['comedy', 'romance']
['drama', 'mystery', 'scifi', 'thriller']
['action', 'comedy', 'crime', 'drama']
['drama']
['crime', 'drama']
['drama']
['thriller']
['adventure', 'animation', 'children', 'comedy', 'fantasy']
['action', 'scifi', 

...

['comedy', 'drama', 'romance']
['action', 'adventure', 'drama', 'war']
['comedy', 'musical']
['action', 'crime', 'drama', 'thriller']
['comedy', 'romance']
['romance', 'scifi']
['drama']
['adventure', 'comedy']
['comedy', 'romance']
['comedy', 'romance']
['action', 'horror', 'scifi', 'thriller']
['drama']
['comedy']
['horror', 'thriller']
['comedy', 'documentary']
['adventure', 'drama', 'horror', 'scifi', 'thriller']
['crime', 'thriller']
['action', 'adventure', 'drama']
['drama', 'romance']
['drama', 'thriller']
['drama', 'romance', 'thriller']
['drama', 'romance']
['drama']
['drama']
['drama']
['action', 'crime', 'drama', 'mystery', 'thriller']
['action', 'horror', 'scifi', 'thriller']
['comedy', 'drama']
['action', 'adventure', 'scifi']
['comedy', 'romance']
['comedy', 'romance']
['drama', 'mystery', 'scifi', 'thriller']
['adventure', 'drama']
['comedy', 'horror']
['drama']
['crime', 'mystery', 'thriller']
['drama']
['action', 'drama', 'horror', 'thriller']
['adventure', 'drama']
['

['adventure', 'animation', 'children', 'comedy', 'fantasy']
['fantasy', 'horror', 'thriller']
['comedy', 'drama']
['comedy', 'drama']
['action', 'comedy', 'crime', 'thriller']
['action', 'adventure', 'thriller']
['adventure', 'children', 'comedy']
['crime', 'drama']
['comedy']
['drama', 'horror', 'mystery', 'thriller']
['drama', 'romance']
['adventure', 'animation', 'children', 'comedy']
['comedy', 'drama']
['action', 'adventure', 'thriller', 'imax']
['drama', 'mystery', 'thriller']
['action', 'scifi', 'thriller']
['comedy', 'drama', 'romance']
['drama']
['animation', 'children', 'comedy']
['drama']
['comedy', 'drama']
['drama']
['horror', 'thriller']
['comedy']
['drama', 'fantasy', 'romance']
['adventure', 'comedy', 'drama', 'fantasy', 'romance']
['comedy', 'drama']
['action', 'adventure', 'fantasy']
['comedy']
['comedy']
['drama', 'fantasy', 'mystery']
['comedy', 'fantasy', 'romance']
['drama', 'romance']
['documentary']
['documentary']
['comedy', 'romance']
['children', 'comedy', 'd

['horror', 'scifi', 'thriller']
['drama']
['action', 'comedy', 'drama']
['action', 'adventure', 'fantasy']
['comedy', 'horror', 'scifi', 'thriller']
['comedy', 'crime', 'drama', 'thriller']
['comedy']
['horror', 'thriller']
['action', 'scifi', 'thriller']
['animation', 'children', 'fantasy', 'imax']
['comedy', 'drama']
['documentary']
['comedy', 'scifi']
['drama', 'horror']
['drama', 'romance']
['horror']
['horror', 'thriller']
['comedy', 'drama']
['drama']
['documentary', 'drama']
['documentary']
['comedy', 'drama']
['comedy', 'drama']
['action', 'fantasy', 'scifi']
['animation', 'scifi']
['action', 'animation', 'comedy', 'horror', 'thriller']
['comedy', 'horror', 'thriller']
['comedy', 'drama']
['comedy']
['action', 'scifi', 'thriller']
['action', 'comedy', 'horror']
['comedy', 'drama', 'mystery']
['drama', 'romance']
['drama']
['documentary']
['comedy', 'romance']
['comedy', 'horror']
['adventure', 'children', 'drama', 'fantasy', 'imax']
['action', 'adventure', 'drama', 'war']
['dra

['action', 'crime', 'drama']
['comedy', 'horror', 'romance']
['comedy', 'drama']
['comedy', 'romance']
['comedy']
['action', 'crime', 'thriller']
['action', 'drama', 'western']
['drama']
['comedy', 'horror']
['comedy', 'horror']
['drama', 'thriller']
['drama', 'musical', 'romance', 'imax']
['horror']
['comedy']
['comedy', 'fantasy', 'horror']
['drama', 'romance']
['drama']
['comedy', 'drama']
['comedy']
['horror', 'mystery', 'thriller']
['action', 'crime', 'drama']
['crime', 'drama', 'thriller']
['animation', 'comedy', 'drama', 'fantasy', 'scifi']
['action', 'animation']
['documentary']
['comedy', 'romance', 'scifi']
['action', 'crime', 'thriller']
['romance', 'scifi', 'thriller']
['crime', 'drama', 'thriller']
['documentary']
['comedy']
['comedy']
['documentary']
['comedy']
['action', 'fantasy', 'horror', 'imax']
['comedy']
['comedy', 'drama']
['drama', 'romance']
['drama', 'romance', 'scifi']
['action', 'thriller']
['drama', 'horror']
['comedy', 'crime']
['crime', 'drama', 'mystery',

['crime', 'drama', 'thriller']
['action', 'adventure', 'romance', 'scifi']
['action', 'adventure', 'fantasy', 'scifi']
['adventure']
['horror']
['drama']
['documentary']
['crime', 'thriller']
['drama', 'fantasy']
['comedy', 'drama']
['adventure', 'drama', 'fantasy']
['action', 'adventure', 'animation']
['action', 'adventure', 'animation', 'fantasy']
['action', 'adventure', 'comedy']
['crime', 'drama', 'horror']
['comedy']
['adventure', 'drama', 'thriller']
['drama']
['comedy', 'drama']
['comedy']
['horror', 'thriller']
['action', 'crime', 'drama', 'scifi']
['animation', 'children', 'comedy', 'drama', 'romance']
['comedy']
['adventure', 'animation', 'comedy']
['animation']
['drama', 'mystery', 'thriller']
['action', 'adventure', 'animation', 'drama', 'fantasy']
['comedy', 'horror', 'thriller']
['adventure', 'drama']
['crime', 'drama']
['horror']
['animation']
['action', 'drama']
['crime', 'drama', 'mystery']
['drama', 'fantasy', 'horror', 'thriller']
['crime', 'thriller']
['romance']
['

In [47]:
len(genre)

1

In [52]:
for i in all_movies.genres:
    i_splitted = i.split("|")
    genre = [genre.lower() for genre in i_splitted]
    see_cos = vect_cos(vectoriser3, [' '.join(genre)])

    print(see_cos)

(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 2 stored elements in Compressed Sparse Row format>, 0.632)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in

(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 2 stored elements in Compressed Sparse Row format>, 0.632)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored eleme

	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 2 stored elements in Compressed Sparse Row format>, 0.632)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse 

	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 2 stored elements in Compressed Sparse Row format>, 0.632)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 spars

(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 2 stored elements in Compressed Sparse Row format>, 0.632)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements 

...

(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 2 stored elements in Compressed Sparse Row format>, 0.632)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored element

	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse 

(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 2 stored elements in Compressed Sparse Row format>, 0.632)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 2 stored elements in

(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 2 stored elements in Compressed Sparse Row format>, 0.632)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements 

	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>, 0.447)
(<1x5 sparse matrix of type '<class 'numpy.int64'>'
	with 0 stored elements in Compressed Sparse Row format>, 0.0)


In [60]:
for i in all_movies.genres:
    i_splitted = i.split("|")
    genre = [genre.lower() for genre in i_splitted]
    see_vect, see_cos = vect_cos(vectoriser3, [' '.join(genre)])
        
    #print(see_vect, see_cos)
    print(see_cos)


0.0
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.447
0.632
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.632
0.447
0.632
0.632
0.447
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.775
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.447
0.0
0.632
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.775
0.0
0.0
0.632
0.447
0.0
0.0
0.0
0.0
0.775
0.0
0.632
0.447
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.632
0.447
0.0
0.0
0.632
0.0
0.0
0.0
0.447
0.0
0.0
0.775
0.0
0.0
0.0
0.0
0.0
0.447
0.447
0.447
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.0
0.447
0.447
0.447
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.447
0.775
0.447
0.0
0.447
0.632
0.632
0.0
0.447
0.0
0.632
0.0
0.775
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.447
0.0
0.632
0.0
0.0
0.447
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.894
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.632
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.632
0.0
0.447
0.447
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447


0.632
0.447
0.632
0.447
0.0
0.447
0.447
0.0
0.447
0.0
0.0
0.632
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.0
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.632
0.632
0.632
0.447
0.447
0.447
0.447
0.447
0.447
0.447
0.447
0.632
0.775
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.447
0.0
0.0
0.0
0.447
0.447
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.447
0.0
0.0
0.632
0.632
0.447
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.632
0.632
0.0
0.0
0.447
0.0
0.0
0.0
0.775
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.632
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.632
0.0
0.447
0.632
0.632
0.447
0.775
0.632
0.632
0.632
0.632
0.632
0.632
0.447
0.632
0.0
0.0
0.0
0.632
0.0
0.447
0.0
0.0
0.0
0.632
0.447
0.447
0.0
0.632
0.632
0.0
0.447
0.0
0.0
0.447
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.775
0.0
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.447
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.775
0.447
0.0
0.0
0.0
0.0
0.0
0.447
0.632
0.447
0.447
0.632
0.0


0.0
0.447
0.0
0.775
0.0
0.0
0.0
0.447
0.0
0.632
0.0
0.0
0.632
0.447
0.0
0.447
0.0
0.0
0.0
0.447
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.632
0.0
0.632
0.632
0.447
0.0
0.632
0.447
0.447
0.447
0.447
0.0
0.632
0.447
0.447
0.0
0.0
0.0
0.447
0.0
0.632
0.632
0.0
0.447
0.0
0.0
0.0
0.0
0.775
0.0
0.0
0.632
0.0
0.447
0.0
0.447
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.632
0.0
0.447
0.0
0.0
0.447
0.0
0.0
0.0
0.632
0.0
0.0
0.775
0.632
0.0
0.447
0.0
0.447
0.447
0.0
0.775
0.447
0.0
0.447
0.0
0.0
0.632
0.447
0.0
0.0
0.775
0.0
0.632
0.632
0.0
0.0
0.447
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.632
0.632
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.447
0.0
0.447
0.447
0.0
0.0
0.0
0.0
0.632
0.0
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.447
0.447
0.447
0.0
0.0
0.0
0.447
0.632
0.0
0.0
0.775
0.0
0.447
0.0
0.447
0.0
0.0
0.632
0.447
0.0
0.0
0.0
0.775
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.447
0.447
0.447
0.0
0.632
0.0
0.0
0.0
0.775
0.0
0.447
0.0
0.0
0.0
0.0
0.

0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.447
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.447
0.0
0.632
0.0
0.447
0.632
0.0
0.0
0.0
0.447
0.447
0.0
0.775
0.0
0.0
0.0
0.447
0.632
0.447
0.0
0.0
0.0
0.447
0.0
0.447
0.632
0.0
0.0
0.447
0.0
0.632
0.0
0.447
0.447
0.0
0.0
0.447
0.447
0.447
0.447
0.0
0.0
0.447
0.447
0.447
0.447
0.0
0.0
0.632
0.0
0.775
0.447
0.447
0.0
0.0
0.0
0.0
0.447
0.632
0.632
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.632
0.632
0.0
0.632
0.447
0.447
0.775
0.0
0.447
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.632
0.0
0.0
0.447
0.0
0.894
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.632
0.775
0.447
0.0
0.0
0.0
0.0
0.447
0.447
0.0
0.0
0.0
0.0
0.632
0.447
0.0
0.447
0.447
0.447
0.447
0.447
0.0
0.0
0.632
0.775
0.0
0.0
0.0
0.447
0.0
0.0
0.447
0.0
0.447
0.0
0.632
0.0
0.632
0.632
0.0
0.0
0.0
0.632
0.775
0.447
0.447
0.0
0.0
0.447
0.447
0.0
0.632
0.632
0.0
0.

0.447
0.632
0.447
0.0
0.447
0.775
0.447
0.0
0.0
0.447
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.632
0.447
0.632
0.447
0.0
0.0
0.775
0.447
0.447
0.0
0.0
0.0
0.0
0.0
0.447
0.447
0.0
0.447
0.0
0.0
0.0
0.447
0.0
0.775
0.0
0.775
0.632
0.447
0.632
0.632
0.447
0.0
0.0
0.0
0.447
0.632
0.0
0.0
0.775
0.0
0.0
0.447
0.632
0.0
0.632
0.447
0.632
0.632
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.447
0.0
0.0
0.447
0.0
0.0
0.447
0.775
0.0
0.775
0.0
0.0
0.0
0.0
0.447
0.0
0.632
0.0
0.0
0.447
0.632
0.0
0.0
0.0
0.632
0.447
0.0
0.0
0.447
0.447
0.0
0.632
0.0
0.447
0.0
0.0
0.0
0.447
0.0
0.632
0.0
0.0
0.447
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.632
0.0
0.775
0.0
0.447
0.632
0.0
0.447
0.0
0.0
0.632
0.0
0.0
0.775
0.0
0.0
0.0
0.447
0.447
0.0
0.447
0.0
0.632
0.447
0.447
0.0
0.0
0.447
0.0
0.447
0.447
0.632
0.0
0.0
0.447
0.447
0.0
0.0
0.775
0.447
0.0
0.0
0.447
0.632
0.447
0.447
0.0
0.447
0.447
0.447
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.775
0.0
0.0
0.0
0.0
0.894
0.447
0.0
0.0
0.447
0.447
0.

0.0
0.0
0.0
0.0
0.775
0.0
0.0
0.447
0.0
0.0
0.632
0.447
0.0
0.0
0.447
0.0
0.0
0.0
0.775
0.0
0.632
0.0
0.0
0.0
0.632
0.447
0.0
0.447
0.632
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.447
0.632
0.447
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.447
0.632
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.632
0.0
0.0
0.447
0.447
0.0
0.632
0.894
0.447
0.0
0.632
0.632
0.632
0.0
0.0
0.447
0.447
0.0
0.447
0.0
0.447
0.632
0.0
0.0
0.447
0.447
0.447
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.632
0.447
0.0
0.0
0.0
0.447
0.632
0.632
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.447
0.447
0.447
0.0
0.0
0.447
0.0
0.0
0.0
0.447
0.632
0.0
0.0
0.0
0.0
0.632
0.447
0.447
0.0
0.0
0.0
0.0
0.447
0.447
0.447
0.447
0.0
0.0
0.447
0.775
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.447
0.0
0.447
0.447
0.0
0.0
0.775
0.0
0.447
0.632
0.0
0.632
0.447
0.0
0.775
0.447
0.0
0.447
0.447
0.0
0.0
0.632
0.0
0.0


In [116]:
all_movies['genre_cosim_score'] = bag
all_movies['genre_cosim_score']

0       0.000
1       0.000
2       0.000
3       0.000
4       0.000
        ...  
9737    0.447
9738    0.000
9739    0.000
9740    0.447
9741    0.000
Name: genre_cosim_score, Length: 9742, dtype: float64

In [117]:
all_movies

index  movieId                                      title  \
0         0        1                           Toy Story (1995)   
1         1        2                             Jumanji (1995)   
2         2        3                    Grumpier Old Men (1995)   
3         3        4                   Waiting to Exhale (1995)   
4         4        5         Father of the Bride Part II (1995)   
...     ...      ...                                        ...   
9737   9737   193581  Black Butler: Book of the Atlantic (2017)   
9738   9738   193583               No Game No Life: Zero (2017)   
9739   9739   193585                               Flint (2017)   
9740   9740   193587        Bungo Stray Dogs: Dead Apple (2018)   
9741   9741   193609        Andrew Dice Clay: Dice Rules (1991)   

                                           genres  genre_cosim_score  
0     Adventure|Animation|Children|Comedy|Fantasy              0.000  
1                      Adventure|Children|Fantasy              0.000  
2                                  Comedy|Romance              0.000  
3                            Comedy|Drama|Romance              0.000  
4                                          Comedy              0.000  
...                                           ...                ...  
9737              Action|Animation|Comedy|Fantasy              0.447  
9738                     Animation|Comedy|Fantasy              0.000  
9739                                        Drama              0.000  
9740                             Action|Animation              0.447  
9741                                       Comedy              0.000  

[9742 rows x 5 columns]

In [115]:
bag

[0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.632,
 0.0,
 0.0,
 0.447,
 0.632,
 0.0,
 0.0,
 0.0,
 0.0,
 0.447,
 0.0,
 0.0,
 0.0,
 0.0,
 0.632,
 0.447,
 0.632,
 0.632,
 0.447,
 0.0,
 0.0,
 0.0,
 0.0,
 0.632,
 0.0,
 0.0,
 0.775,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.447,
 0.0,
 0.447,
 0.447,
 0.0,
 0.632,
 0.0,
 0.0,
 0.632,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.447,
 0.0,
 0.0,
 0.0,
 0.0,
 0.775,
 0.0,
 0.0,
 0.632,
 0.447,
 0.0,
 0.0,
 0.0,
 0.0,
 0.775,
 0.0,
 0.632,
 0.447,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.447,
 0.0,
 0.0,
 0.632,
 0.447,
 0.0,
 0.0,
 0.632,
 0.0,
 0.0,
 0.0,
 0.447,
 0.0,
 0.0,
 0.775,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.447,
 0.447,
 0.447,
 0.447,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.447,
 0.0,
 0.0,
 0.0,
 0.0,
 0.447,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.632,
 0.0,
 0.0,
 0.0,
 0.447,
 0.447,
 0.447,
 0.0,
 0.447,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.447,
 0.775,
 0.447,
 0.0,
 0.447,
 0.632,
 0.632,
 0.0,
 0.447,
 0.0,
 0.632,
 0.0,
 0.775,
 0.632,
 0.0,
 0.0,
 0.0,
 0.0,


In [ ]:
d = []
for p in game.players.passing():
    d.append((p, p.team, p.passer_rating()))

pd.DataFrame(d, columns=('Player', 'Team', 'Passer Rating'))

In [16]:
#นี่แหละใช่เลย
bag = []
for i in all_movies.genres:
    i_splitted = i.split("|")
    genre = [genre.lower() for genre in i_splitted]
    see_vect, see_cos = vect_cos(vectoriser3, [' '.join(genre)])
    print(see_cos)
    bag.append(see_cos)
pd.DataFrame(bag)

0.0
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.447
0.632
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.632
0.447
0.632
0.632
0.447
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.775
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.447
0.0
0.632
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.775
0.0
0.0
0.632
0.447
0.0
0.0
0.0
0.0
0.775
0.0
0.632
0.447
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.632
0.447
0.0
0.0
0.632
0.0
0.0
0.0
0.447
0.0
0.0
0.775
0.0
0.0
0.0
0.0
0.0
0.447
0.447
0.447
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.0
0.447
0.447
0.447
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.447
0.775
0.447
0.0
0.447
0.632
0.632
0.0
0.447
0.0
0.632
0.0
0.775
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.447
0.0
0.632
0.0
0.0
0.447
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.894
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.632
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.632
0.0
0.447
0.447
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447


0.447
0.447
0.447
0.447
0.632
0.775
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.447
0.0
0.0
0.0
0.447
0.447
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.447
0.0
0.0
0.632
0.632
0.447
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.632
0.632
0.0
0.0
0.447
0.0
0.0
0.0
0.775
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.632
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.632
0.0
0.447
0.632
0.632
0.447
0.775
0.632
0.632
0.632
0.632
0.632
0.632
0.447
0.632
0.0
0.0
0.0
0.632
0.0
0.447
0.0
0.0
0.0
0.632
0.447
0.447
0.0
0.632
0.632
0.0
0.447
0.0
0.0
0.447
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.775
0.0
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.447
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.775
0.447
0.0
0.0
0.0
0.0
0.0
0.447
0.632
0.447
0.447
0.632
0.0
0.0
0.0
0.0
0.0
0.775
0.632
0.0
0.0
0.447
0.0
0.0
0.0
0.632
0.632
0.632
0.632
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.447
0.0
0.447
0.447
0.632
0.632
0.447
0.447
0.0
0.0
0.0
0.632
0.0
0.447
0.0
0.447
0.0
0.447
0.

0.0
0.775
0.632
0.0
0.447
0.0
0.447
0.447
0.0
0.775
0.447
0.0
0.447
0.0
0.0
0.632
0.447
0.0
0.0
0.775
0.0
0.632
0.632
0.0
0.0
0.447
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.632
0.632
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.447
0.0
0.447
0.447
0.0
0.0
0.0
0.0
0.632
0.0
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.447
0.447
0.447
0.0
0.0
0.0
0.447
0.632
0.0
0.0
0.775
0.0
0.447
0.0
0.447
0.0
0.0
0.632
0.447
0.0
0.0
0.0
0.775
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.447
0.447
0.447
0.0
0.632
0.0
0.0
0.0
0.775
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.447
0.0
0.447
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.0
0.632
0.447
0.632
0.447
0.447
0.0
0.0
0.632
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.775
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.775
0.0
0.0
0.0
0.0
0.0
0.447
0.775
0.0
0.0
0.0
0.447
0.0
0.447
0.0
0.0
0.447
0.447
0.447
0.0
0.447
0.0
0.775
0.447
0.447
0.0
0.0
0.632
0.447
0.0
0.0
0.0
0.632
0.447
0.0


0.447
0.0
0.775
0.0
0.0
0.0
0.447
0.632
0.447
0.0
0.0
0.0
0.447
0.0
0.447
0.632
0.0
0.0
0.447
0.0
0.632
0.0
0.447
0.447
0.0
0.0
0.447
0.447
0.447
0.447
0.0
0.0
0.447
0.447
0.447
0.447
0.0
0.0
0.632
0.0
0.775
0.447
0.447
0.0
0.0
0.0
0.0
0.447
0.632
0.632
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.632
0.632
0.0
0.632
0.447
0.447
0.775
0.0
0.447
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.632
0.0
0.0
0.447
0.0
0.894
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.632
0.775
0.447
0.0
0.0
0.0
0.0
0.447
0.447
0.0
0.0
0.0
0.0
0.632
0.447
0.0
0.447
0.447
0.447
0.447
0.447
0.0
0.0
0.632
0.775
0.0
0.0
0.0
0.447
0.0
0.0
0.447
0.0
0.447
0.0
0.632
0.0
0.632
0.632
0.0
0.0
0.0
0.632
0.775
0.447
0.447
0.0
0.0
0.447
0.447
0.0
0.632
0.632
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.447
0.0
0.775
0.632
0.0
0.632
0.0
0.0
0.0
0.0
0.0
0.632
0.447
0.0
0.447
0.632
0.447
0.447
0.0
0.632
0.0
0.632
0.632
0.632
0.0
0.0
0.632
0.0
0.632
0.0
0.0
0.632
0.0
0.447
0.632
0.447
0.775
0.0
0.0
0.0
0.632
0.0
0.0
0.632
0.775
0.0
0.632
0.447
0.

0.0
0.447
0.632
0.0
0.0
0.0
0.632
0.447
0.0
0.0
0.447
0.447
0.0
0.632
0.0
0.447
0.0
0.0
0.0
0.447
0.0
0.632
0.0
0.0
0.447
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.447
0.0
0.447
0.632
0.0
0.775
0.0
0.447
0.632
0.0
0.447
0.0
0.0
0.632
0.0
0.0
0.775
0.0
0.0
0.0
0.447
0.447
0.0
0.447
0.0
0.632
0.447
0.447
0.0
0.0
0.447
0.0
0.447
0.447
0.632
0.0
0.0
0.447
0.447
0.0
0.0
0.775
0.447
0.0
0.0
0.447
0.632
0.447
0.447
0.0
0.447
0.447
0.447
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.775
0.0
0.0
0.0
0.0
0.894
0.447
0.0
0.0
0.447
0.447
0.0
0.0
0.0
0.447
0.0
0.447
0.447
0.0
0.0
0.447
0.632
0.0
0.632
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.632
0.0
0.632
0.632
0.632
0.447
0.0
0.447
0.0
0.0
0.447
0.0
0.0
0.632
0.0
0.447
0.0
0.0
0.0
0.775
0.0
0.0
1.0
0.0
0.447
0.447
0.447
0.0
0.447
0.447
0.447
0.632
0.447
0.0
0.447
0.0
0.447
0.0
0.447
0.0
0.0
0.447
0.0
0.0
0.632
0.447
0.0
0.632
0.632
0.632
0.447
0.0
0.632
0.447
0.447
0.447
0.0
0.632
0.0
0.632
0.0
0.894
0.0
0.0
0.447
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.0


0.0
0.0
0.447
0.775
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.447
0.0
0.447
0.447
0.0
0.0
0.775
0.0
0.447
0.632
0.0
0.632
0.447
0.0
0.775
0.447
0.0
0.447
0.447
0.0
0.0
0.632
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.447
0.0
0.0
0.0
0.447
0.0
0.632
0.0
0.447
0.447
0.447
0.0
0.447
0.0
0.632
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.775
0.0
0.447
0.632
0.447
0.447
0.0
0.632
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.0
0.632
0.447
0.0
0.447
0.0
0.447
0.0
0.447
0.447
0.0
0.0
0.0
0.447
0.0
0.0
0.0
0.632
0.0
0.0
0.447
0.0
0.0
0.447
0.0
0.0
0.0
0.0
0.632
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.447
0.447
0.0
0.0
0.447
0.0
0.447
0.447
0.447
0.632
0.447
0.0
0.447
0.447
0.0
0.0
0.632
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.447
0.447
0.0
0.0
0.0
0.447
0.0
0.0
0.447
0.447
0.0
0.447
0.0
0.0
0.0
0.0
0.447
0.0
0.0
0.447
0.632
0.447
0.775
0.0
0.447
0.775
0.0
0.447
0.0
0.0
0.447
0.0
0.447
0.0
0.0
0.632
0.0
0.0
0.447
0.0
0.0


0
0     0.000
1     0.000
2     0.000
3     0.000
4     0.000
...     ...
9737  0.447
9738  0.000
9739  0.000
9740  0.447
9741  0.000

[9742 rows x 1 columns]

In [98]:
bigdata = pd.concat([all_movies, genre_cosim_score], axis =1)
#ok got it here ไปไม้ลื่นได้ะ แต่ต้องแก้หัวตาราง
bigdata.rename(columns={'':'cosim_score'})
bigdata[8:20]


index  movieId                                  title  \
8       8        9                    Sudden Death (1995)   
9       9       10                       GoldenEye (1995)   
10     10       11         American President, The (1995)   
11     11       12     Dracula: Dead and Loving It (1995)   
12     12       13                           Balto (1995)   
13     13       14                           Nixon (1995)   
14     14       15                Cutthroat Island (1995)   
15     15       16                          Casino (1995)   
16     16       17           Sense and Sensibility (1995)   
17     17       18                      Four Rooms (1995)   
18     18       19  Ace Ventura: When Nature Calls (1995)   
19     19       20                     Money Train (1995)   

                                genres      0  
8                               Action  0.447  
9            Action|Adventure|Thriller  0.632  
10                Comedy|Drama|Romance  0.000  
11                       Comedy|Horror  0.000  
12        Adventure|Animation|Children  0.000  
13                               Drama  0.000  
14            Action|Adventure|Romance  0.447  
15                         Crime|Drama  0.000  
16                       Drama|Romance  0.000  
17                              Comedy  0.000  
18                              Comedy  0.000  
19  Action|Comedy|Crime|Drama|Thriller  0.632

In [11]:
bigdata2 = pd.concat([all_movies, genre_cosim_score], axis=1)
bigdata2.columns = ['index', 'movieId', 'title', 'genres', 'cosim_score']
#df.columns = [ 'a', 'x', 'y' ]
bigdata2 # เย่!!

index  movieId                                      title  \
0         0        1                           Toy Story (1995)   
1         1        2                             Jumanji (1995)   
2         2        3                    Grumpier Old Men (1995)   
3         3        4                   Waiting to Exhale (1995)   
4         4        5         Father of the Bride Part II (1995)   
...     ...      ...                                        ...   
9737   9737   193581  Black Butler: Book of the Atlantic (2017)   
9738   9738   193583               No Game No Life: Zero (2017)   
9739   9739   193585                               Flint (2017)   
9740   9740   193587        Bungo Stray Dogs: Dead Apple (2018)   
9741   9741   193609        Andrew Dice Clay: Dice Rules (1991)   

                                           genres  cosim_score  
0     Adventure|Animation|Children|Comedy|Fantasy        0.000  
1                      Adventure|Children|Fantasy        0.000  
2                                  Comedy|Romance        0.000  
3                            Comedy|Drama|Romance        0.000  
4                                          Comedy        0.000  
...                                           ...          ...  
9737              Action|Animation|Comedy|Fantasy        0.447  
9738                     Animation|Comedy|Fantasy        0.000  
9739                                        Drama        0.000  
9740                             Action|Animation        0.447  
9741                                       Comedy        0.000  

[9742 rows x 5 columns]

In [12]:
bigdata2[8:20]

index  movieId                                  title  \
8       8        9                    Sudden Death (1995)   
9       9       10                       GoldenEye (1995)   
10     10       11         American President, The (1995)   
11     11       12     Dracula: Dead and Loving It (1995)   
12     12       13                           Balto (1995)   
13     13       14                           Nixon (1995)   
14     14       15                Cutthroat Island (1995)   
15     15       16                          Casino (1995)   
16     16       17           Sense and Sensibility (1995)   
17     17       18                      Four Rooms (1995)   
18     18       19  Ace Ventura: When Nature Calls (1995)   
19     19       20                     Money Train (1995)   

                                genres  cosim_score  
8                               Action        0.447  
9            Action|Adventure|Thriller        0.632  
10                Comedy|Drama|Romance        0.000  
11                       Comedy|Horror        0.000  
12        Adventure|Animation|Children        0.000  
13                               Drama        0.000  
14            Action|Adventure|Romance        0.447  
15                         Crime|Drama        0.000  
16                       Drama|Romance        0.000  
17                              Comedy        0.000  
18                              Comedy        0.000  
19  Action|Comedy|Crime|Drama|Thriller        0.632

In [19]:
all_movies = pd.concat([all_movies, genre_cosim_score], axis=1) #นี่แหละ
all_movies.columns = ['index', 'movieId', 'title', 'genres', 'cosim_score']

all_movies

index  movieId                                      title  \
0         0        1                           Toy Story (1995)   
1         1        2                             Jumanji (1995)   
2         2        3                    Grumpier Old Men (1995)   
3         3        4                   Waiting to Exhale (1995)   
4         4        5         Father of the Bride Part II (1995)   
...     ...      ...                                        ...   
9737   9737   193581  Black Butler: Book of the Atlantic (2017)   
9738   9738   193583               No Game No Life: Zero (2017)   
9739   9739   193585                               Flint (2017)   
9740   9740   193587        Bungo Stray Dogs: Dead Apple (2018)   
9741   9741   193609        Andrew Dice Clay: Dice Rules (1991)   

                                           genres  cosim_score  
0     Adventure|Animation|Children|Comedy|Fantasy        0.000  
1                      Adventure|Children|Fantasy        0.000  
2                                  Comedy|Romance        0.000  
3                            Comedy|Drama|Romance        0.000  
4                                          Comedy        0.000  
...                                           ...          ...  
9737              Action|Animation|Comedy|Fantasy        0.447  
9738                     Animation|Comedy|Fantasy        0.000  
9739                                        Drama        0.000  
9740                             Action|Animation        0.447  
9741                                       Comedy        0.000  

[9742 rows x 5 columns]

In [14]:
all_movies[20:50]

index  movieId                                              title  \
20     20       21                                  Get Shorty (1995)   
21     21       22                                     Copycat (1995)   
22     22       23                                   Assassins (1995)   
23     23       24                                      Powder (1995)   
24     24       25                           Leaving Las Vegas (1995)   
25     25       26                                     Othello (1995)   
26     26       27                                Now and Then (1995)   
27     27       28                                  Persuasion (1995)   
28     28       29  City of Lost Children, The (Cité des enfants p...   
29     29       30  Shanghai Triad (Yao a yao yao dao waipo qiao) ...   
30     30       31                             Dangerous Minds (1995)   
31     31       32          Twelve Monkeys (a.k.a. 12 Monkeys) (1995)   
32     32       34                                        Babe (1995)   
33     33       36                            Dead Man Walking (1995)   
34     34       38                                It Takes Two (1995)   
35     35       39                                    Clueless (1995)   
36     36       40                    Cry, the Beloved Country (1995)   
37     37       41                                 Richard III (1995)   
38     38       42                             Dead Presidents (1995)   
39     39       43                                 Restoration (1995)   
40     40       44                               Mortal Kombat (1995)   
41     41       45                                  To Die For (1995)   
42     42       46               How to Make an American Quilt (1995)   
43     43       47                        Seven (a.k.a. Se7en) (1995)   
44     44       48                                  Pocahontas (1995)   
45     45       49                       When Night Is Falling (1995)   
46     46       50                         Usual Suspects, The (1995)   
47     47       52                            Mighty Aphrodite (1995)   
48     48       53                                    Lamerica (1994)   
49     49       54                              Big Green, The (1995)   

                                      genres  cosim_score  
20                     Comedy|Crime|Thriller        0.447  
21       Crime|Drama|Horror|Mystery|Thriller        0.632  
22                     Action|Crime|Thriller        0.632  
23                               Drama|SciFi        0.447  
24                             Drama|Romance        0.000  
25                                     Drama        0.000  
26                            Children|Drama        0.000  
27                             Drama|Romance        0.000  
28     Adventure|Drama|Fantasy|Mystery|SciFi        0.632  
29                               Crime|Drama        0.000  
30                                     Drama        0.000  
31                    Mystery|SciFi|Thriller        0.775  
32                            Children|Drama        0.000  
33                               Crime|Drama        0.000  
34                           Children|Comedy        0.000  
35                            Comedy|Romance        0.000  
36                                     Drama        0.000  
37                                 Drama|War        0.000  
38                        Action|Crime|Drama        0.447  
39                                     Drama        0.000  
40                  Action|Adventure|Fantasy        0.447  
41                     Comedy|Drama|Thriller        0.447  
42                             Drama|Romance        0.000  
43                          Mystery|Thriller        0.632  
44  Animation|Children|Drama|Musical|Romance        0.000  
45                             Drama|Romance        0.000  
46                    Crime|Mystery|Thriller        0.632  
47                      Comedy|Drama|Romance        0.000  


In [ ]:
#ok ทีนี้ได้ cosim_score มาแล้ว เราต้องเอาคะแนนจากคอลัมน์นี้ ยัดกลับเข้าไปใน deep learning model เพื่อให้มันเอามาคำนวณด้วย
#ให้น้ำหนักของหนักที่ได้ cosim_score คูณเข้าไปเลยเหรอ?

In [ ]:
movieindex = not_all_ratings['movieId'].unique().tolist()
dl_movie2movie_encoded = {x: i for i, x in enumerate(movieindex)}
dl_movie_encoded2movie = {i: x for i, x in enumerate(movieindex)}

not_all_ratings.loc[:,"movie"] = not_all_ratings["movieId"].map(dl_movie2movie_encoded)
not_all_ratings.loc[:,"rating"] = not_all_ratings["rating"].values.astype(np.float32)

#map userId from ?? to not_all_ratings ?? what do i do with the users??

not_all_user_ids = not_all_ratings["userId"].unique().tolist()
dl_user2user_encoded = {x: i for i, x in enumerate(not_all_user_ids)}
dl_userencoded2user = {i: x for i, x in enumerate(not_all_user_ids)}

not_all_ratings.loc[:,"user"] = not_all_ratings["userId"].map(dl_user2user_encoded)

In [122]:
not_all_ratings["rating"].values.astype(np.float32)

array([4., 4., 4., ..., 5., 5., 3.], dtype=float32)

In [ ]:
map all_movies['genre_cosim_score'] to not_all_rating['cosi']

In [181]:
for i, x in enumerate(movieindex): #เอา movieId จากใน not_all_ratings มาเรียงใหม่ เริ่มตั้งแต่ 0
    print(i,x)
    #คือตัวที่ใช้ map คือ not_all_ratings['movieId'] ไม่ใช่ all_movies['index']

0 1
1 3
2 6
3 47
4 50
5 70
6 101
7 110
8 151
9 157
10 163
11 216
12 223
13 231
14 235
15 260
16 296
17 316
18 333
19 349
20 356
21 362
22 367
23 423
24 441
25 457
26 480
27 500
28 527
29 543
30 552
31 553
32 590
33 592
34 593
35 596
36 608
37 648
38 661
39 673
40 733
41 736
42 780
43 804
44 919
45 923
46 940
47 943
48 954
49 1009
50 1023
51 1024
52 1025
53 1029
54 1030
55 1031
56 1032
57 1042
58 1049
59 1060
60 1073
61 1080
62 1089
63 1090
64 1092
65 1097
66 1127
67 1136
68 1196
69 1197
70 1198
71 1206
72 1208
73 1210
74 1213
75 1214
76 1219
77 1220
78 1222
79 1224
80 1226
81 1240
82 1256
83 1258
84 1265
85 1270
86 1275
87 1278
88 1282
89 1291
90 1298
91 1348
92 1377
93 1396
94 1408
95 1445
96 1473
97 1500
98 1517
99 1552
100 1573
101 1580
102 1587
103 1617
104 1620
105 1625
106 1644
107 1676
108 1732
109 1777
110 1793
111 1804
112 1805
113 1920
114 1927
115 1954
116 1967
117 2000
118 2005
119 2012
120 2018
121 2028
122 2033
123 2046
124 2048
125 2054
126 2058
127 2078
128 2090
129 209

1094 913
1095 1147
1096 1148
1097 1186
1098 1193
1099 1201
1100 1207
1101 1223
1102 1230
1103 1252
1104 1260
1105 1261
1106 1267
1107 1276
1108 1281
1109 1299
1110 1680
1111 2490
1112 2707
1113 2723
1114 3000
1115 3022
1116 3108
1117 3174
1118 3429
1119 3683
1120 3741
1121 4878
1122 4973
1123 5782
1124 6350
1125 7099
1126 7361
1127 27611
1128 27773
1129 48394
1130 78499
1131 1036
1132 1209
1133 1221
1134 1228
1135 1234
1136 1375
1137 2194
1138 3039
1139 3263
1140 3435
1141 3681
1142 4571
1143 6016
1144 6870
1145 7482
1146 31658
1147 64839
1148 68358
1149 80463
1150 81932
1151 82459
1152 431
1153 442
1154 555
1155 653
1156 778
1157 1020
1158 1059
1159 1212
1160 1227
1161 1245
1162 1356
1163 1374
1164 1544
1165 1729
1166 1924
1167 1961
1168 2184
1169 2409
1170 2410
1171 2411
1172 2412
1173 2420
1174 2422
1175 2706
1176 2918
1177 2951
1178 2953
1179 3081
1180 3257
1181 3275
1182 3462
1183 3751
1184 3785
1185 3896
1186 4007
1187 4262
1188 4327
1189 4383
1190 4728
1191 4816
1192 5008
1193 5

2052 52281
2053 53519
2054 54503
2055 55820
2056 56171
2057 56782
2058 56788
2059 60766
2060 61323
2061 64575
2062 66097
2063 68536
2064 71464
2065 29
2066 175
2067 272
2068 334
2069 741
2070 1050
2071 1175
2072 1217
2073 1218
2074 1232
2075 1233
2076 1237
2077 1243
2078 1248
2079 1249
2080 1274
2081 1284
2082 1425
2083 1464
2084 1711
2085 1809
2086 1859
2087 1884
2088 1960
2089 2579
2090 2686
2091 2726
2092 2730
2093 2912
2094 3030
2095 3181
2096 3265
2097 3822
2098 4235
2099 5333
2100 6234
2101 6387
2102 6721
2103 6773
2104 6790
2105 6857
2106 6920
2107 6989
2108 7064
2109 7069
2110 7123
2111 7587
2112 7924
2113 7932
2114 8012
2115 8228
2116 8370
2117 2405
2118 3556
2119 4855
2120 5064
2121 5791
2122 31696
2123 35836
2124 47610
2125 57368
2126 61024
2127 61132
2128 86882
2129 102407
2130 132660
2131 122912
2132 122916
2133 176371
2134 187541
2135 187593
2136 238
2137 421
2138 808
2139 969
2140 1083
2141 1262
2142 1287
2143 1387
2144 1592
2145 2032
2146 2142
2147 2151
2148 2311
2149 2

3063 6460
3064 2739
3065 6058
3066 6541
3067 6564
3068 27660
3069 27706
3070 27808
3071 48043
3072 49130
3073 49649
3074 50804
3075 51086
3076 59501
3077 60072
3078 60126
3079 63072
3080 67734
3081 68554
3082 68848
3083 74228
3084 78105
3085 79357
3086 80693
3087 82461
3088 83369
3089 86911
3090 87430
3091 89492
3092 89864
3093 90866
3094 96861
3095 99149
3096 102123
3097 103042
3098 103341
3099 104863
3100 106002
3101 107348
3102 107406
3103 111360
3104 113741
3105 114662
3106 114678
3107 114935
3108 115210
3109 115680
3110 118696
3111 128512
3112 135518
3113 142222
3114 143355
3115 158966
3116 161131
3117 166534
3118 168250
3119 170827
3120 171763
3121 172591
3122 173925
3123 174053
3124 175303
3125 176601
3126 179401
3127 179819
3128 182715
3129 183611
3130 184471
3131 185031
3132 187595
3133 1202
3134 1965
3135 3088
3136 4105
3137 6104
3138 7022
3139 7132
3140 7387
3141 7980
3142 8376
3143 8873
3144 27846
3145 27904
3146 30810
3147 33779
3148 45728
3149 53000
3150 54259
3151 64285


4038 735
4039 766
4040 791
4041 896
4042 1034
4043 1116
4044 1137
4045 1144
4046 1366
4047 1411
4048 1417
4049 384
4050 464
4051 533
4052 1241
4053 1321
4054 1337
4055 1340
4056 1760
4057 1771
4058 1974
4059 1981
4060 2117
4061 2122
4062 2138
4063 2298
4064 2419
4065 2456
4066 2522
4067 2625
4068 2651
4069 2782
4070 2784
4071 2790
4072 2817
4073 2868
4074 2992
4075 3013
4076 3018
4077 3153
4078 3182
4079 3267
4080 3563
4081 3727
4082 3768
4083 3810
4084 3840
4085 4092
4086 4109
4087 4214
4088 4254
4089 4304
4090 4316
4091 4438
4092 4587
4093 4599
4094 4624
4095 4645
4096 4661
4097 4678
4098 4774
4099 4800
4100 4850
4101 4909
4102 4987
4103 5165
4104 5294
4105 5346
4106 5438
4107 5479
4108 5588
4109 5640
4110 5650
4111 5749
4112 6203
4113 6219
4114 6283
4115 6327
4116 6375
4117 6395
4118 6461
4119 6620
4120 6629
4121 6638
4122 6678
4123 6731
4124 6744
4125 6820
4126 6963
4127 7118
4128 7308
4129 7492
4130 7561
4131 7650
4132 7802
4133 8016
4134 8147
4135 8266
4136 8426
4137 8501
4138 85

5069 3134
5070 3141
5071 3167
5072 3200
5073 3223
5074 3224
5075 3283
5076 3341
5077 3467
5078 3473
5079 3492
5080 3503
5081 3506
5082 4205
5083 4784
5084 5637
5085 5788
5086 5847
5087 6509
5088 6658
5089 6684
5090 7089
5091 7107
5092 8128
5093 8571
5094 8614
5095 26313
5096 31038
5097 2392
5098 27674
5099 55391
5100 66320
5101 242
5102 718
5103 990
5104 1107
5105 1163
5106 1627
5107 1713
5108 1969
5109 1979
5110 2051
5111 2126
5112 2162
5113 2210
5114 2252
5115 2314
5116 2364
5117 2367
5118 2531
5119 2745
5120 2748
5121 2769
5122 2789
5123 2818
5124 2977
5125 2986
5126 3357
5127 3572
5128 3616
5129 3649
5130 3858
5131 3864
5132 3877
5133 4055
5134 4450
5135 4735
5136 6250
5137 6319
5138 6322
5139 6538
5140 5643
5141 45732
5142 1821
5143 1837
5144 3404
5145 4440
5146 5415
5147 5485
5148 5527
5149 5530
5150 5993
5151 6480
5152 4406
5153 7333
5154 7934
5155 26078
5156 26131
5157 33564
5158 2017
5159 2084
5160 4142
5161 4193
5162 4373
5163 4867
5164 4936
5165 4951
5166 5222
5167 5472
5168

6126 26366
6127 26524
6128 44633
6129 58309
6130 5319
6131 44929
6132 48883
6133 1739
6134 2907
6135 3929
6136 4480
6137 121171
6138 131656
6139 140725
6140 146024
6141 128
6142 2348
6143 2766
6144 2859
6145 4529
6146 4711
6147 5137
6148 5820
6149 6027
6150 6337
6151 6370
6152 6713
6153 7564
6154 7815
6155 8011
6156 8015
6157 294
6158 988
6159 1415
6160 7879
6161 8535
6162 7303
6163 388
6164 1807
6165 2240
6166 2377
6167 2445
6168 3733
6169 3807
6170 476
6171 2812
6172 1791
6173 1964
6174 2178
6175 2182
6176 2593
6177 2630
6178 2829
6179 619
6180 886
6181 1255
6182 1327
6183 1497
6184 1503
6185 1992
6186 1993
6187 2170
6188 2448
6189 2498
6190 2517
6191 2846
6192 2974
6193 3235
6194 3511
6195 3652
6196 3676
6197 3696
6198 3857
6199 3908
6200 3938
6201 4030
6202 4143
6203 4224
6204 4248
6205 4533
6206 4683
6207 4748
6208 4771
6209 5076
6210 5080
6211 5127
6212 5401
6213 5452
6214 5556
6215 5569
6216 5667
6217 5833
6218 5853
6219 6196
6220 6220
6221 6379
6222 6405
6223 6559
6224 6664
622

7073 4517
7074 2307
7075 2399
7076 3127
7077 3162
7078 3545
7079 3716
7080 3731
7081 3758
7082 3922
7083 33312
7084 55167
7085 112512
7086 335
7087 882
7088 1351
7089 1352
7090 1601
7091 3648
7092 4434
7093 4942
7094 5113
7095 5288
7096 5468
7097 5706
7098 5979
7099 6021
7100 6654
7101 6656
7102 6836
7103 6899
7104 7104
7105 7304
7106 7756
7107 7834
7108 8138
7109 8610
7110 25959
7111 27692
7112 32139
7113 42556
7114 56837
7115 71302
7116 71999
7117 80748
7118 84799
7119 87287
7120 92760
7121 94262
7122 152
7123 2656
7124 4444
7125 4814
7126 5134
7127 5476
7128 6889
7129 7310
7130 8526
7131 26585
7132 26999
7133 27584
7134 27683
7135 27802
7136 31698
7137 31804
7138 32456
7139 32743
7140 33644
7141 40614
7142 40617
7143 44020
7144 47124
7145 51927
7146 52950
7147 58404
7148 60818
7149 63222
7150 64249
7151 65133
7152 68194
7153 71129
7154 72601
7155 74750
7156 77798
7157 82744
7158 84414
7159 88515
7160 90603
7161 94160
7162 94985
7163 95004
7164 95147
7165 95149
7166 95182
7167 95473


7970 132462
7971 132488
7972 132618
7973 133195
7974 133281
7975 133365
7976 133377
7977 133545
7978 133782
7979 133798
7980 134021
7981 134158
7982 134859
7983 136654
7984 136664
7985 136778
7986 136786
7987 136800
7988 136816
7989 136859
7990 137517
7991 138546
7992 139052
7993 139415
7994 139857
7995 140237
7996 140525
7997 140850
7998 141422
7999 142424
8000 143001
8001 143255
8002 143257
8003 143410
8004 143472
8005 144262
8006 144620
8007 144714
8008 144716
8009 145150
8010 146688
8011 146730
8012 148482
8013 148592
8014 148709
8015 149590
8016 149612
8017 150401
8018 150604
8019 151315
8020 151317
8021 151501
8022 151559
8023 151653
8024 151745
8025 151777
8026 152085
8027 152105
8028 152658
8029 154065
8030 155358
8031 155659
8032 155743
8033 155892
8034 156553
8035 156706
8036 157122
8037 157130
8038 157172
8039 157200
8040 157270
8041 157340
8042 157407
8043 157432
8044 158022
8045 158956
8046 159077
8047 159193
8048 159690
8049 160440
8050 160573
8051 160646
8052 160730
8053

8967 129397
8968 132454
8969 133645
8970 141131
8971 151557
8972 163639
8973 168026
8974 171917
8975 176051
8976 178615
8977 181719
8978 182793
8979 183635
8980 184997
8981 615
8982 1112
8983 4424
8984 113829
8985 114265
8986 124851
8987 478
8988 806
8989 1114
8990 1426
8991 1794
8992 2281
8993 2292
8994 2339
8995 2586
8996 2698
8997 3379
8998 3571
8999 3669
9000 3700
9001 3709
9002 3962
9003 4197
9004 4240
9005 4394
9006 4490
9007 4504
9008 4511
9009 4568
9010 4574
9011 4593
9012 4594
9013 4597
9014 4603
9015 4670
9016 5053
9017 5054
9018 5096
9019 5111
9020 5136
9021 5198
9022 5221
9023 5268
9024 5442
9025 5591
9026 5596
9027 5597
9028 5689
9029 5768
9030 5961
9031 6204
9032 6267
9033 6310
9034 6506
9035 6557
9036 6587
9037 6691
9038 6722
9039 6734
9040 6804
9041 6860
9042 6882
9043 6998
9044 7005
9045 7041
9046 7047
9047 7108
9048 7125
9049 7191
9050 7307
9051 7443
9052 7657
9053 7704
9054 7707
9055 7986
9056 7988
9057 8043
9058 8045
9059 8380
9060 8425
9061 8500
9062 8720
9063 8755

In [188]:
{x:i for i, x in enumerate(movieindex)} #กลับข้างกัน

{1: 0,
 3: 1,
 6: 2,
 47: 3,
 50: 4,
 70: 5,
 101: 6,
 110: 7,
 151: 8,
 157: 9,
 163: 10,
 216: 11,
 223: 12,
 231: 13,
 235: 14,
 260: 15,
 296: 16,
 316: 17,
 333: 18,
 349: 19,
 356: 20,
 362: 21,
 367: 22,
 423: 23,
 441: 24,
 457: 25,
 480: 26,
 500: 27,
 527: 28,
 543: 29,
 552: 30,
 553: 31,
 590: 32,
 592: 33,
 593: 34,
 596: 35,
 608: 36,
 648: 37,
 661: 38,
 673: 39,
 733: 40,
 736: 41,
 780: 42,
 804: 43,
 919: 44,
 923: 45,
 940: 46,
 943: 47,
 954: 48,
 1009: 49,
 1023: 50,
 1024: 51,
 1025: 52,
 1029: 53,
 1030: 54,
 1031: 55,
 1032: 56,
 1042: 57,
 1049: 58,
 1060: 59,
 1073: 60,
 1080: 61,
 1089: 62,
 1090: 63,
 1092: 64,
 1097: 65,
 1127: 66,
 1136: 67,
 1196: 68,
 1197: 69,
 1198: 70,
 1206: 71,
 1208: 72,
 1210: 73,
 1213: 74,
 1214: 75,
 1219: 76,
 1220: 77,
 1222: 78,
 1224: 79,
 1226: 80,
 1240: 81,
 1256: 82,
 1258: 83,
 1265: 84,
 1270: 85,
 1275: 86,
 1278: 87,
 1282: 88,
 1291: 89,
 1298: 90,
 1348: 91,
 1377: 92,
 1396: 93,
 1408: 94,
 1445: 95,
 1473: 96,
 

In [ ]:
ใช้นี้ไม่ได้ ต้องใช้ index ที่มาจาก all_movies

In [ ]:
df = (df1[['ID']].merge(df2, on='ID', how='left')                 
    .rename(columns={'Result2':'Result1','Description':'Result2'}))

In [193]:
#df = (not_all_ratings[['title']].merge(all_movies, on='index', how='left'))
mergedStuff = pd.merge(not_all_ratings, all_movies, on=['title'], how='inner')
mergedStuff

ที่ใช้เวลาอยู่นานก่อนจะเอาสองดาต้าเฟรมมาแปะกันได้คือ
การทำความเข้าใจว่า ทำไม cosim_score ที่ได้มามันไม่ตรงกับชื่อหนัง
เพราะว่าคอลัมน์ movie ที่เอา cosim_score ไปผูกด้วย 
มันไม่ใช่ index ของ all_movies ที่ใช้คำนวณ cosine_similarity() ไงล่ะ
ก็เลยต้องทำคอลัมน์ index ใหม่ ด้วยการ pd.merge()
แต่ไม่เข้าใจพวก left right inner join อีก

userId  movieId_x                             title  rating  movie  \
0            1          1                  Toy Story (1995)     4.0      0   
1            5          1                  Toy Story (1995)     4.0      0   
2            7          1                  Toy Story (1995)     4.5      0   
3           15          1                  Toy Story (1995)     2.5      0   
4           17          1                  Toy Story (1995)     4.5      0   
...        ...        ...                               ...     ...    ...   
100575     610     160341                  Bloodmoon (1997)     2.5   9716   
100576     610     160527  Sympathy for the Underdog (1971)     4.5   9717   
100577     610     160836                     Hazard (2005)     3.0   9718   
100578     610     163937                Blair Witch (2016)     3.5   9719   
100579     610     163981                         31 (2016)     3.5   9720   

        user  cosim_score  index  movieId_y  \
0          0        0.000      0          1   
1          4        0.000      0          1   
2          6        0.000      0          1   
3         14        0.000      0          1   
4         16        0.000      0          1   
...      ...          ...    ...        ...   
100575   609        0.000   9325     160341   
100576   609        0.000   9330     160527   
100577   609        0.000   9342     160836   
100578   609        0.000   9389     163937   
100579   609        0.632   9390     163981   

                                             genres  genre_cosim_score  
0       Adventure|Animation|Children|Comedy|Fantasy              0.000  
1       Adventure|Animation|Children|Comedy|Fantasy              0.000  
2       Adventure|Animation|Children|Comedy|Fantasy              0.000  
3       Adventure|Animation|Children|Comedy|Fantasy              0.000  
4       Adventure|Animation|Children|Comedy|Fantasy              0.000  
...                                             ...                ...  
100575                              Action|Thriller              0.632  
100576                           Action|Crime|Drama              0.447  
100577                        Action|Drama|Thriller              0.632  
100578                              Horror|Thriller              0.447  
100579                                       Horror              0.000  

[100580 rows x 11 columns]

In [194]:
mergedStuff[10:50]เรียงตาม movieId แต่ก่อนหน้านี้เรียงตาม userId นะ
อ่อ เรียงตาม index ว่ะเออออ 
แล้วทำไมมีถึง 9390 มาจากกไหน?? เรามีถึง 9721 นะ

userId  movieId_x             title  rating  movie  user  cosim_score  \
10      32          1  Toy Story (1995)     3.0      0    31          0.0   
11      33          1  Toy Story (1995)     3.0      0    32          0.0   
12      40          1  Toy Story (1995)     5.0      0    39          0.0   
13      43          1  Toy Story (1995)     5.0      0    42          0.0   
14      44          1  Toy Story (1995)     3.0      0    43          0.0   
15      45          1  Toy Story (1995)     4.0      0    44          0.0   
16      46          1  Toy Story (1995)     5.0      0    45          0.0   
17      50          1  Toy Story (1995)     3.0      0    49          0.0   
18      54          1  Toy Story (1995)     3.0      0    53          0.0   
19      57          1  Toy Story (1995)     5.0      0    56          0.0   
20      63          1  Toy Story (1995)     5.0      0    62          0.0   
21      64          1  Toy Story (1995)     4.0      0    63          0.0   
22      66          1  Toy Story (1995)     4.0      0    65          0.0   
23      68          1  Toy Story (1995)     2.5      0    67          0.0   
24      71          1  Toy Story (1995)     5.0      0    70          0.0   
25      73          1  Toy Story (1995)     4.5      0    72          0.0   
26      76          1  Toy Story (1995)     0.5      0    75          0.0   
27      78          1  Toy Story (1995)     4.0      0    77          0.0   
28      82          1  Toy Story (1995)     2.5      0    81          0.0   
29      86          1  Toy Story (1995)     4.0      0    85          0.0   
30      89          1  Toy Story (1995)     3.0      0    88          0.0   
31      90          1  Toy Story (1995)     3.0      0    89          0.0   
32      91          1  Toy Story (1995)     4.0      0    90          0.0   
33      93          1  Toy Story (1995)     3.0      0    92          0.0   
34      96          1  Toy Story (1995)     5.0      0    95          0.0   
35      98          1  Toy Story (1995)     4.5      0    97          0.0   
36     103          1  Toy Story (1995)     4.0      0   102          0.0   
37     107          1  Toy Story (1995)     4.0      0   106          0.0   
38     112          1  Toy Story (1995)     3.0      0   111          0.0   
39     119          1  Toy Story (1995)     3.5      0   118          0.0   
40     121          1  Toy Story (1995)     4.0      0   120          0.0   
41     124          1  Toy Story (1995)     4.0      0   123          0.0   
42     130          1  Toy Story (1995)     3.0      0   129          0.0   
43     132          1  Toy Story (1995)     2.0      0   131          0.0   
44     134          1  Toy Story (1995)     3.0      0   133          0.0   
45     135          1  Toy Story (1995)     4.0      0   134          0.0   
46     137          1  Toy Story (1995)     4.0      0   136          0.0   
47     140          1  Toy Story (1995)     3.0      0   139          0.0   
48     141          1  Toy Story (1995)     4.0      0   140          0.0   
49     144          1  Toy Story (1995)     3.5      0   143          0.0   

    index  movieId_y                                       genres  \
10      0          1  Adventure|Animation|Children|Comedy|Fantasy   
11      0          1  Adventure|Animation|Children|Comedy|Fantasy   
12      0          1  Adventure|Animation|Children|Comedy|Fantasy   
13      0          1  Adventure|Animation|Children|Comedy|Fantasy   
14      0          1  Adventure|Animation|Children|Comedy|Fantasy   
15      0          1  Adventure|Animation|Children|Comedy|Fantasy   
16      0          1  Adventure|Animation|Children|Comedy|Fantasy   
17      0          1  Adventure|Animation|Children|Comedy|Fantasy   
18      0          1  Adventure|Animation|Children|Comedy|Fantasy   
19      0          1  Adventure|Animation|Children|Comedy|Fantasy   
20      0          1  Adventure|Animation|Children|Comedy|Fantasy   
21      0         

In [195]:
mergedStuff[8000:8050]

userId  movieId_x          title  rating  movie  user  cosim_score  \
8000     524       1214   Alien (1979)     3.0     75   523          0.0   
8001     527       1214   Alien (1979)     5.0     75   526          0.0   
8002     532       1214   Alien (1979)     5.0     75   531          0.0   
8003     533       1214   Alien (1979)     4.0     75   532          0.0   
8004     555       1214   Alien (1979)     5.0     75   554          0.0   
8005     560       1214   Alien (1979)     3.5     75   559          0.0   
8006     561       1214   Alien (1979)     4.5     75   560          0.0   
8007     562       1214   Alien (1979)     4.5     75   561          0.0   
8008     570       1214   Alien (1979)     3.5     75   569          0.0   
8009     571       1214   Alien (1979)     2.0     75   570          0.0   
8010     572       1214   Alien (1979)     4.0     75   571          0.0   
8011     573       1214   Alien (1979)     4.5     75   572          0.0   
8012     577       1214   Alien (1979)     4.0     75   576          0.0   
8013     580       1214   Alien (1979)     4.0     75   579          0.0   
8014     590       1214   Alien (1979)     4.5     75   589          0.0   
8015     594       1214   Alien (1979)     4.0     75   593          0.0   
8016     596       1214   Alien (1979)     4.0     75   595          0.0   
8017     597       1214   Alien (1979)     5.0     75   596          0.0   
8018     599       1214   Alien (1979)     5.0     75   598          0.0   
8019     600       1214   Alien (1979)     2.5     75   599          0.0   
8020     603       1214   Alien (1979)     5.0     75   602          0.0   
8021     606       1214   Alien (1979)     4.0     75   605          0.0   
8022     607       1214   Alien (1979)     3.0     75   606          0.0   
8023     608       1214   Alien (1979)     4.0     75   607          0.0   
8024     610       1214   Alien (1979)     4.5     75   609          0.0   
8025       1       1219  Psycho (1960)     2.0     76     0          0.0   
8026       4       1219  Psycho (1960)     4.0     76     3          0.0   
8027       7       1219  Psycho (1960)     5.0     76     6          0.0   
8028      16       1219  Psycho (1960)     3.0     76    15          0.0   
8029      18       1219  Psycho (1960)     4.5     76    17          0.0   
8030      19       1219  Psycho (1960)     4.0     76    18          0.0   
8031      39       1219  Psycho (1960)     5.0     76    38          0.0   
8032      41       1219  Psycho (1960)     4.0     76    40          0.0   
8033      59       1219  Psycho (1960)     5.0     76    58          0.0   
8034      68       1219  Psycho (1960)     4.5     76    67          0.0   
8035      74       1219  Psycho (1960)     4.5     76    73          0.0   
8036      84       1219  Psycho (1960)     4.0     76    83          0.0   
8037      91       1219  Psycho (1960)     5.0     76    90          0.0   
8038      98       1219  Psycho (1960)     5.0     76    97          0.0   
8039     105       1219  Psycho (1960)     4.5     76   104          0.0   
8040     116       1219  Psycho (1960)     2.5     76   115          0.0   
8041     122       1219  Psycho (1960)     4.0     76   121          0.0   
8042     132       1219  Psycho (1960)     4.0     76   131          0.0   
8043     137       1219  Psycho (1960)     5.0     76   136          0.0   
8044     156       1219  Psycho (1960)     4.5     76   155          0.0   
8045     160       1219  Psycho (1960)     3.0     76   159          0.0   
8046     168       1219  Psycho (1960)     4.0     76   167          0.0   
8047     177       1219  Psycho (1960)     5.0     76   176          0.0   
8048     182       1219  Psycho (1960)     3.0     76   181          0.0   
8049     202       1219  Psycho (1960)     4.0     76   201          0.0   

      index  movieId_y        genres  genre_cosim_score  
8000    915       1214  Horror|SciFi              0.447  
8001    915  

In [196]:
mergedStuff[100000:100020]

userId  movieId_x                                              title  \
100000     599      46574                             OH in Ohio, The (2006)   
100001     599      47721         Red Balloon, The (Ballon rouge, Le) (1956)   
100002     599      47793                            Puffy Chair, The (2006)   
100003     599      49110                  Mom and Dad Save the World (1992)   
100004     599      51545          Pusher III: I'm the Angel of Death (2005)   
100005     599      53022              Wheels on Meals (Kuai can che) (1984)   
100006     610      53022              Wheels on Meals (Kuai can che) (1984)   
100007     599      53143                                    Fay Grim (2006)   
100008     599      53161  I'm a Cyborg, But That's OK (Saibogujiman kwen...   
100009     610      53161  I'm a Cyborg, But That's OK (Saibogujiman kwen...   
100010     599      53450                Legend of Sleepy Hollow, The (1980)   
100011     599      54274                        I Know Who Killed Me (2007)   
100012     599      54908                                      Taxi 4 (2007)   
100013     599      55036                                       Gotti (1996)   
100014     599      55061                                   Electroma (2006)   
100015     599      55205                                   Interview (2007)   
100016     599      55207                                    Cashback (2004)   
100017     599      56022                           Harrison Bergeron (1995)   
100018     599      57499            Heaven and Earth (Ten to Chi to) (1990)   
100019     599      58306                                      Mongol (2007)   

        rating  movie  user  cosim_score  index  movieId_y  \
100000     2.5   9156   598        0.000   6241      46574   
100001     3.5   9157   598        0.632   6281      47721   
100002     2.5   9158   598        0.000   6285      47793   
100003     2.0   9159   598        0.000   6340      49110   
100004     2.5   9160   598        0.000   6429      51545   
100005     3.0   9161   598        0.000   6484      53022   
100006     4.5   9161   609        0.000   6484      53022   
100007     2.0   9162   598        0.000   6493      53143   
100008     3.0   9163   598        0.000   6494      53161   
100009     3.0   9163   609        0.000   6494      53161   
100010     1.5   9164   598        0.000   6502      53450   
100011     0.5   9165   598        0.000   6531      54274   
100012     2.0   9166   598        0.000   6552      54908   
100013     2.5   9167   598        0.000   6560      55036   
100014     1.0   9168   598        0.447   6562      55061   
100015     2.5   9169   598        0.447   6575      55205   
100016     3.0   9170   598        0.000   6576      55207   
100017     2.0   9171   598        0.000   6623      56022   
100018     3.0   9172   598        0.000   6666      57499   
100019     2.5   9173   598        0.447   6699      58306   

                                     genres  genre_cosim_score  
100000                               Comedy              0.000  
100001                     Children|Fantasy              0.000  
100002                        Drama|Romance              0.000  
100003                         Comedy|SciFi              0.447  
100004  Action|Comedy|Drama|Horror|Thriller              0.632  
100005          Action|Comedy|Crime|Romance              0.447  
100006          Action|Comedy|Crime|Romance              0.447  
100007                      Action|Thriller              0.632  
100008           Comedy|Drama|Romance|SciFi              0.447  
100009           Comedy|Drama|Romance|SciFi              0.447  
100010                Comedy|Fantasy|Horror              0.000  
100011                 Crime|Drama|Thriller              0.447  
100012                        Action|Comedy              0.447  
100013                          Crime|Drama              0.000  
100014                          Drama|SciFi      

In [199]:
merged2[8000:8050]

userId  movieId_x                                              title  \
8000      56        457                               Fugitive, The (1993)   
8001      56        480                               Jurassic Park (1993)   
8002      56        493                           Menace II Society (1993)   
8003      56        592                                      Batman (1989)   
8004      56        593                   Silence of the Lambs, The (1991)   
8005      56        733                                   Rock, The (1996)   
8006      56        786                                      Eraser (1996)   
8007      57          1                                   Toy Story (1995)   
8008      57          6                                        Heat (1995)   
8009      57         10                                   GoldenEye (1995)   
8010      57         11                     American President, The (1995)   
8011      57         21                                  Get Shorty (1995)   
8012      57         32          Twelve Monkeys (a.k.a. 12 Monkeys) (1995)   
8013      57         39                                    Clueless (1995)   
8014      57         50                         Usual Suspects, The (1995)   
8015      57         52                            Mighty Aphrodite (1995)   
8016      57         65                                    Bio-Dome (1996)   
8017      57         69                                      Friday (1995)   
8018      57         70                         From Dusk Till Dawn (1996)   
8019      57         89                                Nick of Time (1995)   
8020      57         95                                Broken Arrow (1996)   
8021      57        104                               Happy Gilmore (1996)   
8022      57        107                      Muppet Treasure Island (1996)   
8023      57        110                                  Braveheart (1995)   
8024      57        112         Rumble in the Bronx (Hont faan kui) (1995)   
8025      57        141                               Birdcage, The (1996)   
8026      57        150                                   Apollo 13 (1995)   
8027      57        151                                     Rob Roy (1995)   
8028      57        153                              Batman Forever (1995)   
8029      57        158                                      Casper (1995)   
8030      57        160                                       Congo (1995)   
8031      57        162                                       Crumb (1994)   
8032      57        171                                     Jeffrey (1995)   
8033      57        185                                    Net, The (1995)   
8034      57        198                                Strange Days (1995)   
8035      57        208                                  Waterworld (1995)   
8036      57        224                            Don Juan DeMarco (1995)   
8037      57        227                                   Drop Zone (1994)   
8038      57        234                                Exit to Eden (1994)   
8039      57        235                                     Ed Wood (1994)   
8040      57        260          Star Wars: Episode IV - A New Hope (1977)   
8041      57        265  Like Water for Chocolate (Como agua para choco...   
8042      57        272                 Madness of King George, The (1994)   
8043      57        296                                Pulp Fiction (1994)   
8044      57        303                     Quick and the Dead, The (1995)   
8045      57        305               Ready to Wear (Pret-A-Porter) (1994)   
8046      57        316                                    Stargate (1994)   
8047      57        329                      Star Trek: Generations (1994)   
8048      57        349                    Clear and Present Danger (1994)   
8049      57        355                            Flintstones, The (1994)   

      rating  movie  user  

In [16]:
all_movies.loc[all_movies['index'] == 6556]


index  movieId                 title               genres
6556   6556    54995  Planet Terror (2007)  Action|Horror|SciFi

In [40]:
allmoviesindex = all_movies['index']
#not_all_ratings.loc[:,"movie"] = not_all_ratings["movieId"].map(dl_movie2movie_encoded)
#dl_movie2movie_encoded = {x: i for i, x in enumerate(movieindex)}
#merged3= pd. merge(not_all_ratings, bigdata2, on=['title'], how='left')
#{x:i for i,x in enumerate(allmoviesindex)}
not_all_ratings.loc[:, "index"] = not_all_ratings['title'].map(all_movies['index'])
not_all_ratings.loc[:, "index"]
#map all_movies['index'] to not_all_ratings['title']

0        NaN
1        NaN
2        NaN
3        NaN
4        NaN
          ..
100831   NaN
100832   NaN
100833   NaN
100834   NaN
100835   NaN
Name: index, Length: 100474, dtype: float64

In [ ]:
mapping = dict(df2[['store_code', 'warehouse']].values)
df1['warehouse'] = df1.store.map(mapping)

In [18]:
mapping = dict(all_movies[['index', 'cosim_score']].values)
not_all_ratings['cosim_score'] = not_all_ratings['title'].map(mapping)

<ipython-input-18-e37eb70bc0b3>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  not_all_ratings['cosim_score'] = not_all_ratings['title'].map(mapping)


In [ ]:
map all_movies['index'] to not_all_ratings['title'] then take the corresponding cosim_score

In [21]:
not_all_ratings['index'] = not_all_ratings['title'].map(all_movies['index'])

<ipython-input-21-3ed23bd407ba>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  not_all_ratings['index'] = not_all_ratings['title'].map(all_movies['index'])


In [17]:
not_all_ratings['cosim_score'] = merged2['cosim_score']
not_all_ratings #length is not equal so i still have NaN
#let's leave it here for now and do some overall meaning of semantic search

<ipython-input-17-f610d70d00de>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  not_all_ratings['cosim_score'] = merged2['cosim_score']


userId  movieId                           title  rating  movie  user  \
0            1        1                Toy Story (1995)     4.0      0     0   
1            1        3         Grumpier Old Men (1995)     4.0      1     0   
2            1        6                     Heat (1995)     4.0      2     0   
3            1       47     Seven (a.k.a. Se7en) (1995)     5.0      3     0   
4            1       50      Usual Suspects, The (1995)     5.0      4     0   
...        ...      ...                             ...     ...    ...   ...   
100831     610   166534                    Split (2017)     4.0   3117   609   
100832     610   168248   John Wick: Chapter Two (2017)     5.0   2032   609   
100833     610   168250                  Get Out (2017)     5.0   3118   609   
100834     610   168252                    Logan (2017)     5.0   1389   609   
100835     610   170875  The Fate of the Furious (2017)     3.0   2870   609   

        cosim_score  
0             0.000  
1             0.000  
2             0.632  
3             0.632  
4             0.632  
...             ...  
100831          NaN  
100832          NaN  
100833          NaN  
100834          NaN  
100835          NaN  

[100474 rows x 7 columns]

In [19]:
bigdata2 = pd.concat([all_movies, genre_cosim_score], axis=1)
bigdata2.columns = ['index', 'movieId', 'title', 'genres', 'cosim_score']
#df.columns = [ 'a', 'x', 'y' ]
bigdata2 # เย่!!

ValueError: Length mismatch: Expected axis has 6 elements, new values have 5 elements

In [12]:
all_movies

index  movieId                                      title  \
0         0        1                           Toy Story (1995)   
1         1        2                             Jumanji (1995)   
2         2        3                    Grumpier Old Men (1995)   
3         3        4                   Waiting to Exhale (1995)   
4         4        5         Father of the Bride Part II (1995)   
...     ...      ...                                        ...   
9737   9737   193581  Black Butler: Book of the Atlantic (2017)   
9738   9738   193583               No Game No Life: Zero (2017)   
9739   9739   193585                               Flint (2017)   
9740   9740   193587        Bungo Stray Dogs: Dead Apple (2018)   
9741   9741   193609        Andrew Dice Clay: Dice Rules (1991)   

                                           genres  cosim_score  
0     Adventure|Animation|Children|Comedy|Fantasy        0.000  
1                      Adventure|Children|Fantasy        0.000  
2                                  Comedy|Romance        0.000  
3                            Comedy|Drama|Romance        0.000  
4                                          Comedy        0.000  
...                                           ...          ...  
9737              Action|Animation|Comedy|Fantasy        0.447  
9738                     Animation|Comedy|Fantasy        0.000  
9739                                        Drama        0.000  
9740                             Action|Animation        0.447  
9741                                       Comedy        0.000  

[9742 rows x 5 columns]

In [21]:
genre_cosim_score

0
0     0.000
1     0.000
2     0.000
3     0.000
4     0.000
...     ...
9737  0.447
9738  0.000
9739  0.000
9740  0.447
9741  0.000

[9742 rows x 1 columns]

In [22]:
merged3= pd. merge(not_all_ratings, all_movies, on=['title'], how='left')
merged3

userId  movieId_x                           title  rating  movie  \
0            1          1                Toy Story (1995)     4.0      0   
1            1          3         Grumpier Old Men (1995)     4.0      1   
2            1          6                     Heat (1995)     4.0      2   
3            1         47     Seven (a.k.a. Se7en) (1995)     5.0      3   
4            1         50      Usual Suspects, The (1995)     5.0      4   
...        ...        ...                             ...     ...    ...   
100575     610     166534                    Split (2017)     4.0   3117   
100576     610     168248   John Wick: Chapter Two (2017)     5.0   2032   
100577     610     168250                  Get Out (2017)     5.0   3118   
100578     610     168252                    Logan (2017)     5.0   1389   
100579     610     170875  The Fate of the Furious (2017)     3.0   2870   

        user  cosim_score_x  index  movieId_y  \
0          0          0.000      0          1   
1          0          0.000      2          3   
2          0          0.632      5          6   
3          0          0.632     43         47   
4          0          0.632     46         50   
...      ...            ...    ...        ...   
100575   609            NaN   9434     166534   
100576   609            NaN   9461     168248   
100577   609            NaN   9462     168250   
100578   609            NaN   9463     168252   
100579   609            NaN   9503     170875   

                                             genres  cosim_score_y  
0       Adventure|Animation|Children|Comedy|Fantasy          0.000  
1                                    Comedy|Romance          0.000  
2                             Action|Crime|Thriller          0.632  
3                                  Mystery|Thriller          0.632  
4                            Crime|Mystery|Thriller          0.632  
...                                             ...            ...  
100575                        Drama|Horror|Thriller          0.447  
100576                        Action|Crime|Thriller          0.632  
100577                                       Horror          0.000  
100578                                 Action|SciFi          0.632  
100579                  Action|Crime|Drama|Thriller          0.632  

[100580 rows x 11 columns]

In [ ]:
merged3= pd. merge(not_all_ratings, all_movies, on=['title'], how='left')
ถูกถึง on=['title'] แล้ว แต่หลังจากนั้นต้องเป็น return cosim_score มาใส่ใน not_all_ratings['cosim_score']
not_all_ratings['cosim_score'] = np.where(not_all_ratings['title'] == all_movies['title']) --> all_movies['cosim_score']

In [ ]:
จะคิดหาวิธี map ไปถึงเมื่อไหร่ เริ่มได้แล้ว ก้เอา merged3 ไปใช้นั่นแหละ

ไม่ได้ ยังไงก็ไม่ได้ มันไม่สวย

In [ ]:
มันต้องเป็น not_all_ratings ที่ map มาจาก not_all_ratings เอง

In [13]:
not_all_ratings

userId  movieId                           title  rating  movie  user
0            1        1                Toy Story (1995)     4.0      0     0
1            1        3         Grumpier Old Men (1995)     4.0      1     0
2            1        6                     Heat (1995)     4.0      2     0
3            1       47     Seven (a.k.a. Se7en) (1995)     5.0      3     0
4            1       50      Usual Suspects, The (1995)     5.0      4     0
...        ...      ...                             ...     ...    ...   ...
100831     610   166534                    Split (2017)     4.0   3117   609
100832     610   168248   John Wick: Chapter Two (2017)     5.0   2032   609
100833     610   168250                  Get Out (2017)     5.0   3118   609
100834     610   168252                    Logan (2017)     5.0   1389   609
100835     610   170875  The Fate of the Furious (2017)     3.0   2870   609

[100474 rows x 6 columns]

In [ ]:
df1 = df1.merge(df2[['weeknum', 'datetime']], on=['weeknum'])

In [20]:
not_all_ratings = not_all_ratings.merge(all_movies[['title', 'cosim_score']], on=['title'])
not_all_ratings #wuuuhuwwww คือแค่กำหนดว่า ที่เอามาจาก df2(all_movies) แค่สองคอลัมน์พอนะ 
#แล้วเมิร์จด้วย title จะได้ไม่ต้องมานั่งลบคอลัมน์

userId  movieId                             title  rating  movie  \
0            1        1                  Toy Story (1995)     4.0      0   
1            5        1                  Toy Story (1995)     4.0      0   
2            7        1                  Toy Story (1995)     4.5      0   
3           15        1                  Toy Story (1995)     2.5      0   
4           17        1                  Toy Story (1995)     4.5      0   
...        ...      ...                               ...     ...    ...   
100575     610   160341                  Bloodmoon (1997)     2.5   9716   
100576     610   160527  Sympathy for the Underdog (1971)     4.5   9717   
100577     610   160836                     Hazard (2005)     3.0   9718   
100578     610   163937                Blair Witch (2016)     3.5   9719   
100579     610   163981                         31 (2016)     3.5   9720   

        user  cosim_score  
0          0        0.000  
1          4        0.000  
2          6        0.000  
3         14        0.000  
4         16        0.000  
...      ...          ...  
100575   609        0.632  
100576   609        0.447  
100577   609        0.632  
100578   609        0.447  
100579   609        0.000  

[100580 rows x 7 columns]

In [21]:
not_all_ratings['cosim_score'] #ต้องไปเอา ratings ออกด้วยสิ ไม่งั้นจะ leak

0         0.000
1         0.000
2         0.000
3         0.000
4         0.000
          ...  
100575    0.632
100576    0.447
100577    0.632
100578    0.447
100579    0.000
Name: cosim_score, Length: 100580, dtype: float64

In [ ]:
ต้องไปเอาหนังที่ดูแล้วออกจาก all_movies!

In [22]:
movies_not_watched

index  movieId                                      title  \
0         0        1                           Toy Story (1995)   
1         1        2                             Jumanji (1995)   
2         2        3                    Grumpier Old Men (1995)   
3         3        4                   Waiting to Exhale (1995)   
4         4        5         Father of the Bride Part II (1995)   
...     ...      ...                                        ...   
9737   9737   193581  Black Butler: Book of the Atlantic (2017)   
9738   9738   193583               No Game No Life: Zero (2017)   
9739   9739   193585                               Flint (2017)   
9740   9740   193587        Bungo Stray Dogs: Dead Apple (2018)   
9741   9741   193609        Andrew Dice Clay: Dice Rules (1991)   

                                           genres  fake_id  prediction  
0     Adventure|Animation|Children|Comedy|Fantasy        1    0.521305  
1                      Adventure|Children|Fantasy        1    0.527310  
2                                  Comedy|Romance        1    0.518026  
3                            Comedy|Drama|Romance        1    0.513871  
4                                          Comedy        1    0.510786  
...                                           ...      ...         ...  
9737              Action|Animation|Comedy|Fantasy        1    0.515109  
9738                     Animation|Comedy|Fantasy        1    0.523695  
9739                                        Drama        1    0.507459  
9740                             Action|Animation        1    0.501938  
9741                                       Comedy        1    0.499157  

[9739 rows x 6 columns]

In [ ]:
ทีนี้ ได้ dataframe ที่ต้องการออกมาแล้วยังไงต่อ
ต้องใส่คอลัมน์นี้ เพิ่ิมเข้าไปในโมเดล เพื่อให้ RecommenderNet มี word embedding อันนี้
แต่นี้เรามีเป็นเลขแล้วนะ
ไม่ใช่เป็น word เออ แต่ user กับ movie ก็เป็นเลขเหมือนกัน

In [205]:
merged2.drop(['cosim_score','movieId_y'], axis=1)
#ยังมี row เยอะไป ต้องเอาหนังที่ดูแล้วออกด้วย

userId  movieId_x                           title  rating  movie  \
0            1          1                Toy Story (1995)     4.0      0   
1            1          3         Grumpier Old Men (1995)     4.0      1   
2            1          6                     Heat (1995)     4.0      2   
3            1         47     Seven (a.k.a. Se7en) (1995)     5.0      3   
4            1         50      Usual Suspects, The (1995)     5.0      4   
...        ...        ...                             ...     ...    ...   
100575     610     166534                    Split (2017)     4.0   3117   
100576     610     168248   John Wick: Chapter Two (2017)     5.0   2032   
100577     610     168250                  Get Out (2017)     5.0   3118   
100578     610     168252                    Logan (2017)     5.0   1389   
100579     610     170875  The Fate of the Furious (2017)     3.0   2870   

        user  index                                       genres  \
0          0      0  Adventure|Animation|Children|Comedy|Fantasy   
1          0      2                               Comedy|Romance   
2          0      5                        Action|Crime|Thriller   
3          0     43                             Mystery|Thriller   
4          0     46                       Crime|Mystery|Thriller   
...      ...    ...                                          ...   
100575   609   9434                        Drama|Horror|Thriller   
100576   609   9461                        Action|Crime|Thriller   
100577   609   9462                                       Horror   
100578   609   9463                                 Action|SciFi   
100579   609   9503                  Action|Crime|Drama|Thriller   

        genre_cosim_score  
0                   0.000  
1                   0.000  
2                   0.632  
3                   0.632  
4                   0.632  
...                   ...  
100575              0.447  
100576              0.632  
100577              0.000  
100578              0.632  
100579              0.632  

[100580 rows x 9 columns]

In [206]:
all_movies.loc[all_movies['index'] == 9461]


index  movieId                          title                 genres  \
9461   9461   168248  John Wick: Chapter Two (2017)  Action|Crime|Thriller   

      genre_cosim_score  
9461              0.632

In [23]:
all_movies.loc[all_movies['title'] == 'Heat (1995)']

index  movieId        title                 genres  cosim_score
5      5        6  Heat (1995)  Action|Crime|Thriller        0.632

In [159]:
not_all_ratings.loc[not_all_ratings['movieId'] == 47]

userId  movieId                        title  rating  movie  user  \
3           1       47  Seven (a.k.a. Se7en) (1995)     5.0      3     0   
303         4       47  Seven (a.k.a. Se7en) (1995)     2.0      3     3   
588         6       47  Seven (a.k.a. Se7en) (1995)     4.0      3     5   
1033        8       47  Seven (a.k.a. Se7en) (1995)     4.0      3     7   
1355       13       47  Seven (a.k.a. Se7en) (1995)     5.0      3    12   
...       ...      ...                          ...     ...    ...   ...   
95865     601       47  Seven (a.k.a. Se7en) (1995)     4.0      3   600   
95981     602       47  Seven (a.k.a. Se7en) (1995)     5.0      3   601   
97376     606       47  Seven (a.k.a. Se7en) (1995)     3.0      3   605   
98679     608       47  Seven (a.k.a. Se7en) (1995)     4.5      3   607   
99538     610       47  Seven (a.k.a. Se7en) (1995)     5.0      3   609   

       cosim_score  
3              0.0  
303            0.0  
588            0.0  
1033           0.0  
1355           0.0  
...            ...  
95865          0.0  
95981          0.0  
97376          0.0  
98679          0.0  
99538          0.0  

[203 rows x 7 columns]

In [161]:
#how to find the genres of Seven, how to find its row in all_movies??

In [164]:
all_movies.loc[all_movies['title'] == 'Seven (a.k.a. Se7en) (1995)']

index  movieId                        title            genres  \
43     43       47  Seven (a.k.a. Se7en) (1995)  Mystery|Thriller   

    genre_cosim_score  
43              0.632

In [ ]:
#แสดงว่าที่เอาไปแปะใน not_all_ratings ยังผิดอยู่ ไม่สามารถ link จาก not_all_ratings['movie'] ไปที่ corresponding cosim_score

In [190]:
not_all_ratings.loc[not_all_ratings['movie'] == 3]

userId  movieId                        title  rating  movie  user  \
3           1       47  Seven (a.k.a. Se7en) (1995)     5.0      3     0   
303         4       47  Seven (a.k.a. Se7en) (1995)     2.0      3     3   
588         6       47  Seven (a.k.a. Se7en) (1995)     4.0      3     5   
1033        8       47  Seven (a.k.a. Se7en) (1995)     4.0      3     7   
1355       13       47  Seven (a.k.a. Se7en) (1995)     5.0      3    12   
...       ...      ...                          ...     ...    ...   ...   
95865     601       47  Seven (a.k.a. Se7en) (1995)     4.0      3   600   
95981     602       47  Seven (a.k.a. Se7en) (1995)     5.0      3   601   
97376     606       47  Seven (a.k.a. Se7en) (1995)     3.0      3   605   
98679     608       47  Seven (a.k.a. Se7en) (1995)     4.5      3   607   
99538     610       47  Seven (a.k.a. Se7en) (1995)     5.0      3   609   

       cosim_score  
3              0.0  
303            0.0  
588            0.0  
1033           0.0  
1355           0.0  
...            ...  
95865          0.0  
95981          0.0  
97376          0.0  
98679          0.0  
99538          0.0  

[203 rows x 7 columns]

In [28]:
ratings2 = movies_not_watched.loc[:,'prediction with genres bias']

highest_score = ratings2[ratings2.argsort()[-10:]][::-1]

recom_movie_titles = movies_not_watched.loc[movies_not_watched.loc[:,'prediction with genres bias'].isin(highest_score)]
#movies_not_watched.loc[movies_not_watched['index'].isin(top_ratings_indices)]
recom_movie_titles


KeyError: 'prediction with genres bias'

In [36]:
movies_not_watched_bias.loc[:,'prediction with genres bias'] = movies_not_watched_bias['prediction']*movies_not_watched_bias['cosim_score']
#movies_not_watched_bias
ratings2 = movies_not_watched_bias['prediction with genres bias']
highest_score = ratings2[ratings2.argsort()[-10:]][::-1]
highest_score



7383    0.517067
6810    0.506389
7335    0.476398
8131    0.475608
3878    0.470822
7422    0.468448
1393    0.467324
6164    0.466690
6483    0.465657
7636    0.464614
Name: prediction with genres bias, dtype: float64

In [49]:
movies_not_watched_bias.loc[:,'prediction with genres bias'] = movies_not_watched_bias['prediction']*movies_not_watched_bias['cosim_score']
#movies_not_watched_bias
ratings2 = movies_not_watched_bias['prediction with genres bias']
highest_score = ratings2[ratings2.argsort()[-10:]][::-1]

recom_movie_titles = movies_not_watched_bias.loc[movies_not_watched_bias['prediction with genres bias'].isin(highest_score)]
#movies_not_watched.loc[movies_not_watched['index'].isin(top_ratings_indices)]
recom_movie_titles

#ได้แล้วโว้ยยยยยยย
แต่ก็งั้นๆแหละปะ ได้แต่หนังดาดๆ

index  movieId                                  title  \
1393   1391     1909  X-Files: Fight the Future, The (1998)   
3878   3873     5445                 Minority Report (2002)   
6164   6151    44191                  V for Vendetta (2006)   
6483   6470    52722                    Spider-Man 3 (2007)   
6810   6797    60684                        Watchmen (2009)   
7335   7324    77561                      Iron Man 2 (2010)   
7383   7372    79132                       Inception (2010)   
7422   7411    80363        Resident Evil: Afterlife (2010)   
7636   7625    87306                         Super 8 (2011)   
8131   8120   101076           G.I. Joe: Retaliation (2013)   

                                               genres  fake_id  prediction  \
1393             Action|Crime|Mystery|Sci-Fi|Thriller        1    0.522734   
3878             Action|Crime|Mystery|Sci-Fi|Thriller        1    0.526647   
6164                      Action|Sci-Fi|Thriller|IMAX        1    0.522024   
6483            Action|Adventure|Sci-Fi|Thriller|IMAX        1    0.520869   
6810        Action|Drama|Mystery|Sci-Fi|Thriller|IMAX        1    0.506389   
7335            Action|Adventure|Sci-Fi|Thriller|IMAX        1    0.532883   
7383  Action|Crime|Drama|Mystery|Sci-Fi|Thriller|IMAX        1    0.517067   
7422               Action|Horror|Sci-Fi|Thriller|IMAX        1    0.523991   
7636                     Mystery|Sci-Fi|Thriller|IMAX        1    0.519702   
8131            Action|Adventure|Sci-Fi|Thriller|IMAX        1    0.532000   

      cosim_score  prediction with genres bias  
1393        0.894                     0.467324  
3878        0.894                     0.470822  
6164        0.894                     0.466690  
6483        0.894                     0.465657  
6810        1.000                     0.506389  
7335        0.894                     0.476398  
7383        1.000                     0.517067  
7422        0.894                     0.468448  
7636        0.894                     0.464614  
8131        0.894                     0.475608

In [42]:
all_movies.loc[all_movies['index'] == 7383]


index  movieId                                              title  \
7383   7383    79333  Watch Out for the Automobile (Beregis avtomobi...   

                    genres  cosim_score    0  
7383  Comedy|Crime|Romance          0.0  0.0

In [44]:
movies_not_watched_bias.loc[movies_not_watched_bias['index'] == 6810]


index  movieId                                     title  \
6823   6810    60904  Heart of a Dog (Sobachye serdtse) (1988)   

                   genres  fake_id  prediction  cosim_score  \
6823  Comedy|Drama|Sci-Fi        1    0.499221        0.447   

      prediction with genres bias  
6823                     0.223152

In [47]:
movies_not_watched_bias.loc[movies_not_watched_bias['index'] == 7335]


index  movieId            title        genres  fake_id  prediction  \
7346   7335    77893  Merantau (2009)  Action|Drama        1    0.507306   

      cosim_score  prediction with genres bias  
7346        0.447                     0.226766

In [48]:
movies_not_watched_bias.loc[movies_not_watched_bias['index'] == 8131]


index  movieId                title genres  fake_id  prediction  \
8142   8131   101531  Phil Spector (2013)  Drama        1    0.507829   

      cosim_score  prediction with genres bias  
8142          0.0                          0.0